# setup

## import stuff

In [ ]:
# magics
%matplotlib inline

# regulary used
from copy import deepcopy
import glob
import matplotlib as mpl
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from mpl_toolkits.axes_grid1 import make_axes_locatable
import numpy as np
import os
import pandas as pd
from pathlib import Path
import pickle
import re
from scipy import constants as const
from scipy import integrate
from scipy import optimize
import tempfile
import xml.etree.ElementTree as ET

# from own toolbox
import gromacstools as gt
run_bash = gt.general.run_bash
WorkingDir = gt.general.WorkingDir

# own constants
class oconst: pass
oconst.k_gro = const.k * const.N_A * 1e-3
oconst.h_gro = const.h * const.N_A * 1e-3 * 1e12
oconst.rec_cm_per_THz = 1e12 / const.c / 100

# notebook wide variables
jobids = []

## notebook specific constants

In [ ]:
project_label = "20-ihnc"
working_dir_base = os.path.join("/home/marvin/research/simulations/work", project_label)
template_dir = os.path.join("/home/marvin/research/simulations/work/", project_label, "template")

oconst.epsilon = 1 # in kJ/mol
oconst.sigma = 1 # in nm

## remote computing resource

In [ ]:
# make adjustments here
remote_host = 'franklin'
remote_partition = 'enzo'
remote_ntasks_argument = '--exclusive'
#remote_ntasks_argument = '--ntasks=12'

In [ ]:
remote_dir_base = os.path.join("/home/mbernhardt/run", project_label)

remote_spack_gromacs_module = {
    'enzogpu': '/yfcl45y  # gromacs@2019 build_type=RelWithDebInfo +cuda~double~mpi~plumed+rdtscp+shared simd=AVX2_256',
    'mammut-b': '/6wmvagj  # gromacs@2019.5 build_type=RelWithDebInfo ~cuda~double~double_precision+hwloc~mdrun_only~mpi+openmp~plumed+rdtscp+shared simd=SSE2',
    'mammut-c': '/2skeqyg  # gromacs@2019.3 build_type=RelWithDebInfo ~cuda~double~mpi~plumed+rdtscp+shared simd=AVX_256',
    'enzo': '/qmpnnzb  # gromacs@2019.5 build_type=RelWithDebInfo ~cuda~double~mpi~plumed+rdtscp+shared simd=SSE2',
    'biby': '/rf37djz  # gromacs@2019.3 build_type=RelWithDebInfo ~cuda~double~mpi~plumed~rdtscp+shared simd=SSE2',
    'berger-b': '/2skeqyg  # gromacs@2019.3 build_type=RelWithDebInfo ~cuda~double~mpi~plumed+rdtscp+shared simd=AVX_256',
}[remote_partition]

remote_header = f"""#!/bin/sh
#SBATCH --job-name=md
#SBATCH {remote_ntasks_argument}
#SBATCH --time=24:00:00
#SBATCH --partition={remote_partition}

set -eo pipefail  # -u does not work with VOTCA and/or conda?
shopt -s expand_aliases
alias gmx="gmx -quiet"

module purge
spack load /e4wa6u5  # fftw@3.3.8~mpi~openmp~pfft_patches precision=double,float
spack load /p2rbc3m  # boost@1.72~python
spack load {remote_spack_gromacs_module}

source /home/mbernhardt/software/votca/bin/VOTCARC.bash

source /home/mbernhardt/software/miniconda3/etc/profile.d/conda.sh
conda activate
"""
remote_footer = ''

## systems

In [ ]:
atomtypes = {
    'lj': {'name': 'lj', 'mass': 39.948},
    'OW': {'name': 'OW', 'mass': 15.9994},
    'HW1': {'name': 'HW1', 'mass':  1.008},
    'HW2': {'name': 'HW2', 'mass':  1.008},
    'C': {'name': 'C', 'mass': 12.011},
    'H': {'name': 'H', 'mass': 1.008}
}
    
lj_atoms = [atomtypes[atom] for atom in ['lj']]
lj_moltypes = [{'name': "LJ", 'atoms': lj_atoms, 'nmols': 5000,
                'sigma': 1, 'abc_indicators': [0, 0, 0, 0], 'rot_treat': 'f',
                'cg_repr': ['A']}]

spce_atoms = [atomtypes[atom] for atom in ['OW', 'HW1', 'HW2']]
spce_moltypes = [{'name': "SOL", 'atoms': spce_atoms, 'nmols': 5000,
                  'sigma': 2, 'abc_indicators': [1, 2, 0, -1], 'rot_treat': 'f',
                  'cg_repr': ['A']}]

hexane_atoms = [atomtypes[atom] for atom in ['C', 'H', 'H', 'H'] + ['C', 'H', 'H']*4 + ['C', 'H', 'H', 'H']]
hexane_moltypes = [{'name': "HEX", 'atoms': hexane_atoms, 'nmols': 2000,
                  'sigma': 2, 'abc_indicators': None, 'rot_treat': 'f',
                  'cg_repr': ['A', 'A']}]

naphtalene_atoms = [atomtypes[atom] for atom in ['C']*10 + ['H']*8]
naphtalene_moltypes = [{'name': "NAP", 'atoms': naphtalene_atoms, 'nmols': 2000,
                        'sigma': 4, 'abc_indicators': None, 'rot_treat': 'f',
                        'cg_repr': ['A', 'A', 'A', 'A']}]

systems = []
systems.append({'name': "lj/near-critical", 'type': 'lj', 'r_max_u': 2.5, 'r_extend_g': 5.0,
                'temperature_red': 1.316, 'density_red': 0.304,
                'moltypes': deepcopy(lj_moltypes), 'tags': []})
systems.append({'name': "lj/near-triple", 'type': 'lj', 'r_max_u': 2.5, 'r_extend_g': 9.0,
                'temperature_red': 1.0, 'density_red': 0.8,
                'moltypes': deepcopy(lj_moltypes), 'tags': []})
systems.append({'name': "spce", 'type': 'spce', 'r_max_u': 0.8, 'r_extend_g': 1.6,
                'temperature': 273.15 + 25, 'density': 0.998,
                'moltypes': deepcopy(spce_moltypes), 'tags': []})
systems.append({'name': "hexane", 'type': 'hexane', 'r_max_u': 1.2, 'r_extend_g': 2.4,
                'temperature': 273.15 + 0, 'density': 0.67,
                'moltypes': deepcopy(hexane_moltypes), 'tags': ['has_intra']})
systems.append({'name': "naphtalene", 'type': 'naphtalene', 'r_max_u': 1.2, 'r_extend_g': 2.4,
                'temperature': 273.15 + 100, 'density': 0.99,
                'moltypes': deepcopy(naphtalene_moltypes), 'tags': ['has_intra']})

def calc_volume_from_red(density_red, natoms, sigma):
    """
    density_red in reduced units
    n_atoms in int
    sigma in nm
    """
    density = density_red / sigma**3  # in atoms per nm^3
    return natoms / density  # in nm^3

def calc_volume_from_real(density, molar_mass, n_mols):
    """
    density in g/mL
    molar_mass in g/mol
    n_mols
    """
    system_mass = n_mols * molar_mass / const.N_A  # in g
    volume = system_mass / density  # in mL
    return volume / 1e-21 # in nm³

# some additional fields for later use
for system_nr, system in enumerate(systems):
    system['top'] = gt.top.Topology()
    system['top'].load_simple_top(system['moltypes'])
    if 'temperature' not in system:
        if 'temperature_red' in system:
            system['temperature'] = oconst.epsilon * system['temperature_red'] / oconst.k_gro
    if 'volume' not in system:
        if 'density_red' in system:
            system['volume'] = calc_volume_from_red(system['density_red'],
                                                    system['top'].natoms(),
                                                    oconst.sigma)
        if 'density' in system:
            molar_mass = sum((mol.mass for mol in system['top'].mols())) / system['top'].nmols()
            system['volume'] = calc_volume_from_real(system['density'], molar_mass, system['top'].nmols())
    assert system['volume']**(1/3) / 2 - 0.2 > system['r_extend_g'], "system to small for RDF"
            
# easier sometimes to querry this
systems_dict = {system['name']: system for system in systems}

# print
pd.DataFrame(systems)

## inverse settings

lj/near-triple does not converge when starting from hncinit, only from biinit, weird ...

In [ ]:
inverse_settings = [
    {'name': 'ibi-hncinit-ibiintra',
     'method': {'method': 'ibi'},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'none',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    {'name': 'imc0.3-hncinit-ibiintra',
     'method': {'method': 'imc',
                'regul': 0.3},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'none',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    {'name': 'hncn-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'newton',
                'closure': 'hnc',
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'none',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    {'name': 'hncned-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'newton',
                'closure': 'hnc',
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'sample',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    
    {'name': 'hncnedf-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'newton',
                'closure': 'hnc',
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'sample',
     'cut-jacobian': 'false',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    {'name': 'hncnex-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'newton',
                'closure': 'hnc',
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'extrapolate',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    {'name': 'hncgned-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'gauss-newton',
                'closure': 'hnc',
                'gn-ranges': (2, 2),
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': 'sample',
     'iterations-max': 21,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
    {'name': 'ibi-biinit-ibiintra',
     'method': {'method': 'ibi'},
     'init': {'method': 'bi'},
     'intra-treat': 'ibi',
     'extend-g': 'none',
     'iterations-max': 1,
     'system-types': ['lj', 'spce', 'hexane', 'naphtalene'],
    },
]

invsets_dict = {invset['name']: invset for invset in inverse_settings}
pd.DataFrame(inverse_settings)

In [ ]:
invset_short_names = {
    'ibi-hncinit-ibiintra': 'IBI',
    'imc0.3-hncinit-ibiintra': 'IMC',
    'hncn-hncinit-ibiintra': 'HNCN (sd)',
    'hncned-hncinit-ibiintra': 'HNCN (jc)',
    'hncnedf-hncinit-ibiintra': 'HNCN',
    'hncnex-hncinit-ibiintra': 'HNCN (ex)',
    'hncgned-hncinit-ibiintra': 'HNCGN',
}

In [ ]:
def iterator_sys_inv(systems, inverse_settings, return_indices=False):
    return (
        (((s, i), (system, inverse_setting,
                   os.path.join(system['name'], inverse_setting['name']))
         ) if return_indices
         else (system, inverse_setting, os.path.join(system['name'], inverse_setting['name'])))
            for s, system in enumerate(systems)
            for i, inverse_setting in enumerate(inverse_settings)
        if system['type'] in inverse_setting['system-types'])

In [ ]:
for (s,i), (system, inverse_setting, working_dir) in iterator_sys_inv(systems, inverse_settings, return_indices=True):
    print(s, f'{i:2d}', working_dir)

## often used helper functions

In [ ]:
def check_job_stati(jobids, remote_host):
    stati = gt.remote.check_slurm_jobs(jobids, remote_host)

    # print status for each job
    completed_jobids = []
    for jobid, status in zip(jobids, stati):
        print(jobid, status)
        if (status in ('FAILED', 'COMPLETED', None)
            or status.startswith('CANCELLED')):
            completed_jobids.append(jobid)

    # remove jobids which are completed
    new_jobids = [jobid for jobid in jobids if jobid not in completed_jobids]
    return new_jobids

In [ ]:
def print_red(string):
    print(f"\x1b[31m{string}\x1b[0m")

# MD

In [ ]:
systems_to_run = []
#systems_to_run += systems
#systems_to_run += [system for system in systems if system['type'] == 'lj']
systems_to_run += [system for system in systems if system['name'] == 'lj/near-triple']

for system in systems:
    if system in systems_to_run:
        print(system['name'])
    else:
        print_red(system['name'])

## prepare MD

In [ ]:
for system in systems_to_run:
    
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')
          
    with WorkingDir(working_dir):
        # make dirs and copy template files
        run_bash("mkdir -p equi1 equi2 prod topol")
        run_bash(f"cp {template_dir}/{system['type']}/aa/topol.top topol/")
        run_bash(f"cp {template_dir}/{system['type']}/aa/single-*.gro equi1/")
        run_bash(f"cp {template_dir}/{system['type']}/aa/equi1.mdp equi1/grompp.mdp")
        run_bash(f"cp {template_dir}/{system['type']}/aa/equi2.mdp equi2/grompp.mdp")
        run_bash(f"cp {template_dir}/{system['type']}/aa/prod.mdp prod/grompp.mdp")
        run_bash(f"cp {template_dir}/{system['type']}/map.xml topol/")
        run_bash(f"cp {template_dir}/empty.gro equi1/empty.gro")
        
        # for calculating distributions and inverting them
        run_bash(f"cp {template_dir}/{system['type']}/settings.xml topol/settings.xml")

        # run length
        gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',  10000)
        gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps', 100000)
        gt.mdp.set_parameter("prod/grompp.mdp", 'nsteps', 2000000)
        
        # set temperature
        gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', system['temperature'])
        gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t', system['temperature'])
                 
        # set max r of rdf
        tree = ET.parse('topol/settings.xml')
        root = tree.getroot()
        root.find('non-bonded').find('max').text = str(system['r_extend_g'])
        tree.write('topol/settings.xml')

## fill box

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')
          
    with WorkingDir(working_dir):
        box_edge = system['volume']**(1/3)
          
        # empty box with volume
        run_bash(f"gmx editconf -box {box_edge} {box_edge} {box_edge} -o equi1/conf.gro -f equi1/empty.gro")
        
        # insert water
        n_water = sum((moltype['nmols'] for moltype in system['moltypes'] if moltype['name'] == 'SOL'))
        if n_water > 0:
            run_bash(f"gmx solvate -cs spc216.gro -box {box_edge} {box_edge} {box_edge} -maxsol {n_water} -scale 0.52 -o equi1/conf.gro")
            run_bash("rm -f equi1/\#conf.gro.*")
          
        # insert other molecules
        for moltype in (moltype for moltype in system['moltypes'] if moltype['name'] != 'SOL'):
            n_mols = moltype['nmols']
            mt_name = moltype['name']
            run_bash(f"gmx insert-molecules -f equi1/conf.gro -o equi1/conf.gro -ci equi1/single-{mt_name}.gro -nmol {n_mols} -try 100 -scale 0.5")
            run_bash("rm -f equi1/\#conf.gro.*")

        # check
        n_atoms_inserted = gt.gro.get_natoms("equi1/conf.gro")
        n_atoms_wanted = system['top'].natoms()
        if n_atoms_inserted != n_atoms_wanted:
            print(n_atoms_inserted, n_atoms_wanted)
            raise Exception("not enough molecules inserted")

## run and calc RDF and bond distr. on cluster

In [ ]:
for system in systems_to_run:
    
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')
    remote_dir = os.path.join(remote_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        # mkdir
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

        # copy simulation files to remote
        filelist = ["equi1/conf.gro */grompp.mdp topol"]
        gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

        # commands to be run on compute nodes
        script = remote_header + fr"""
pushd equi1
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top
        gmx mdrun -pin on -nt $SLURM_JOB_CPUS_PER_NODE
    fi
    rm -f \#*
popd

pushd equi2
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro
        gmx mdrun -pin on -nt $SLURM_JOB_CPUS_PER_NODE
    fi
    rm -f \#*
popd

pushd prod
    if [[ ! -f confout.gro ]]; then
        gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro
        gmx mdrun -x $JOBTMP/traj_comp.xtc -pin on -nt $SLURM_JOB_CPUS_PER_NODE
        ls -lh $JOBTMP
        csg_stat --top topol.tpr --options ../topol/settings.xml --trj $JOBTMP/traj_comp.xtc \
            --cg ../topol/map.xml --nt=$SLURM_JOB_CPUS_PER_NODE --ext dist.new
        {'if true; then' if 'has_intra' in system['tags'] else 'if false; then'}
            csg_stat --top topol.tpr --options ../topol/settings.xml --trj $JOBTMP/traj_comp.xtc \
                --cg ../topol/map.xml --nt=$SLURM_JOB_CPUS_PER_NODE --include-intra --ext dist-incl.new
        fi
    fi
    rm -f \#*
popd
""" + remote_footer

        jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
        print(jobid)
        if jobid != None:
            jobids.append(jobid)

## check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

## copy results from cluster

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')
    remote_dir = os.path.join(remote_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        filelist = ["*/*.edr", "prod/*.dist*.new*", "*/confout.gro", "*/topol.tpr"]
        exclude = "traj*"
        gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')
          
    with WorkingDir(working_dir):
        print("equilibration 2")
        show_energy_graphs(["Temperature"], edr_file="equi2/ener.edr")
        print("production")
        show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
        show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")

## copy target distributions to for-cg folder

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        run_bash("mkdir -p for-cg")
        pathlist = Path(".").glob('prod/*.dist.new')
        for path in pathlist:
            interaction_name = str(path).split('/')[-1].split('.dist.')[0]
            run_bash(f"cp {str(path)} for-cg/{interaction_name}.dist.tgt")
        pathlist = Path(".").glob('prod/*-*.dist-incl.new')
        for path in pathlist:
            interaction_name = str(path).split('/')[-1].split('.dist-incl.')[0]
            run_bash(f"cp {str(path)} for-cg/{interaction_name}.dist-incl.tgt")

## manually check and edit all target distributions
votca throws errors if there is a zero value after a first small value in a distribution

## show target distributions

In [ ]:
with mpl.rc_context(rc={'figure.dpi': 100}):
    for system in systems_to_run:
        print(f"system {system['name']}")
        working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')

        with WorkingDir(working_dir):
            pathlist = Path(".").glob('for-cg/*.dist.tgt')
            for path in pathlist:
                path_in_str = str(path)
                interaction_name = path_in_str.split('/')[-1].split('.dist.')[0]
                data = np.loadtxt(path_in_str, dtype=np.str, comments=['#', '@'])
                r = data[:, 0].astype(np.float)
                g = data[:, 1].astype(np.float)

                fig, ax = plt.subplots(figsize=(3, 2))
                ax.plot(r, g)
                #ax.set_xlim(0, system['r_max_u'])
                #ax.set_xlim(min(r), max(r))
                #ax.set_yscale('log')
                #ax.set_ylim(0)
                #ax.set_xlabel("r / nm")
                ax.set_ylabel("")
                ax.vlines(system['r_max_u'], 0.1, 0.9, linestyles=':', color='r')
                ax.vlines(system['r_extend_g'], 0.1, 0.9, linestyles='--')
                ax.grid()
                ax.set_title(interaction_name)
                fig.tight_layout()
                fig.savefig(os.path.join(working_dir_base, 'figures', f"target-rdf_{system['name'].replace('/', '-')}.png"), dpi=300)
                plt.show()

## map prod/confout.gro to for-cg/conf.gro

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        run_bash(f"mkdir -p for-cg")
        run_bash(f"csg_map --top prod/topol.tpr --trj prod/confout.gro --cg topol/map.xml --out for-cg/conf.gro")

## invert non-bonded distribution with HNC

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        pathlist = Path(".").glob('prod/*.dist.new')
        for path in pathlist:
            interaction_name = str(path).split('/')[-1].split('.dist.')[0]
            if path.exists() and '-' in interaction_name:
                kBT = system['temperature'] * oconst.k_gro
                n_intra = ' '.join((str(len(moltype['cg_repr'])) for moltype in system['moltypes']))
                density = system['top'].nmols() / system['volume']
                if 'has_intra' in system['tags']:
                    run_bash(f"csg_call dist invert_iie potential_guess "
                             f"--kBT {kBT} "
                             f"--closure hnc "
                             f"--densities {density} "
                             f"--n-intra {n_intra} "
                             f"--cut-off {system['r_max_u']} "
                             f"--g-tgt {path} "
                             f"--G-tgt prod/{interaction_name}.dist-incl.new "
                             f"--U-out for-cg/{interaction_name}.pot.hnc")
                else:
                    run_bash(f"csg_call dist invert_iie potential_guess "
                             f"--kBT {kBT} "
                             f"--closure hnc "
                             f"--densities {density} "
                             f"--n-intra {n_intra} "
                             f"--cut-off {system['r_max_u']} "
                             f"--g-tgt {path} "
                             f"--U-out for-cg/{interaction_name}.pot.hnc")
                print(f'  HNC inversion done for {interaction_name}')

## invert bonded potentials

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        pathlist = Path(".").glob('for-cg/*.dist.tgt')
        for path in pathlist:
            interaction_name = str(path).split('/')[-1].split('.dist.')[0]
            if path.exists() and interaction_name.startswith(('bond', 'angle', 'dihedral')):
                kBT = system['temperature'] * oconst.k_gro
                run_bash(f"csg_call dist invert --kbT {kBT} {path} for-cg/{interaction_name}.pot.in")
                print(f'  basic inversion done for {interaction_name}')

In [ ]:
for system in systems_to_run:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')

    with WorkingDir(working_dir):
        pathlist = Path(".").glob('for-cg/*.pot.hnc')
        for path in pathlist:
            interaction_name = str(path).split('/')[-1].split('.dist.')[0]
            if path.exists() and '-' in interaction_name:
                data, header = gt.xvg.load(path)
                with plt.style.context(['science', 'notebook', 'muted']):
                    fig, ax = plt.subplots()
                    ax.plot(data[0], data[1])
                    ax.set_ylim(-3, 10)
                    ax.set_xlabel(r"$r$")
                    ax.set_ylabel(r"$U(r)$")
                    plt.show()

# Inverse Coarse-Graining

In [ ]:
systems_to_cg = []
systems_to_cg += [system for system in systems if system['name'] in (
    #'lj/near-critical',
    'lj/near-triple',
    #'spce',
    #'hexane',
    #'naphtalene',
)]

inverse_settings_for_cg = []
inverse_settings_for_cg += [invset for invset in inverse_settings if invset['name'] in [
    'ibi-hncinit-ibiintra',
    'imc0.3-hncinit-ibiintra',
    'hncn-hncinit-ibiintra',
    'hncned-hncinit-ibiintra',
    'hncnedf-hncinit-ibiintra',
    'hncnex-hncinit-ibiintra',
    'hncgned-hncinit-ibiintra',
    'hncgn-1.5-2-hncinit-ibiintra',
    'hncgn-2-2-hncinit-ibiintra',
    'hncgn-1.05-2-hncinit-ibiintra',
    'ibi-biinit-ibiintra',
]]

for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_cg, inverse_settings_for_cg):
    print(system['name'], inverse_setting['name'])

## prepare inverse

In [ ]:
def indent(elem, level=0):
    """indent xml"""
    i = "\n" + level*"  "
    if len(elem):
        if not elem.text or not elem.text.strip():
            elem.text = i + "  "
        if not elem.tail or not elem.tail.strip():
            elem.tail = i
        for elem in elem:
            indent(elem, level+1)
        if not elem.tail or not elem.tail.strip():
            elem.tail = i
    else:
        if level and (not elem.tail or not elem.tail.strip()):
            elem.tail = i

In [ ]:
# show bonded interactions of each system
for system in systems_to_cg:
    print(f"system {system['name']}")
    working_dir = os.path.join(working_dir_base, system['name'], 'fine-grained')
          
    with WorkingDir(working_dir):
        if 'has_intra' in system['tags']:
            tree = ET.parse('topol/settings.xml')
            tree_map = ET.parse('topol/map.xml')
            cg_bondeds = tree_map.find('topology').find('cg_bonded').findall('*')
            for cg_bonded in cg_bondeds:
                interaction_type = cg_bonded.tag
                interaction_name = cg_bonded.find('name').text
                print(interaction_type, interaction_name)
                xpath = f"./bonded/[name='{interaction_name}']"
                table_name = tree.find(xpath).find('inverse').find('gromacs').find('table').text

In [ ]:
for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_cg, inverse_settings_for_cg):
    print(working_dir)
          
    with WorkingDir(working_dir):
        
        # initial structure, target distr. and bond stuff
        run_bash(f"cp ../fine-grained/for-cg/* .")
        
        # template stuff
        run_bash(f"cp {template_dir}/{system['type']}/cg/topol.top topol.top")
        run_bash(f"cp {template_dir}/{system['type']}/cg/grompp.mdp grompp.mdp")
        run_bash(f"cp {template_dir}/{system['type']}/table.xvg table.xvg")
        run_bash(f"cp {template_dir}/{system['type']}/settings.xml settings.xml")
        if 'has_intra' in system['tags']:
            run_bash(f"cp {template_dir}/{system['type']}/cg/map.xml map.xml")
            run_bash(f"cp {template_dir}/{system['type']}/cg/map.xml map.xml")
            
        # do i need this one alway or just when has_intra?
        run_bash(f"cp {template_dir}/{system['type']}/cg/topology.xml topology.xml")
        
        # settings.xml
        tree = ET.parse('settings.xml')
        root = tree.getroot()
        # general settings
        root.find('inverse').find('iterations_max').text = str(inverse_setting['iterations-max'])
        root.find('inverse').find('kBT').text = str(oconst.k_gro * system['temperature'])
        root.find('inverse').find('gromacs').find('table_end').text = str(system['r_max_u']
                                       + float(gt.mdp.get_parameter("grompp.mdp", 'table-extension'))
                                       + 0.1)
        root.find('inverse').find('method').text = inverse_setting['method']['method']
        # non-bonded potetinal settings
        if 'gn-ranges' in inverse_setting:
            r_max_g = str(system['r_max_u']) * inverse_setting['gn-ranges'][1]
        else:
            if inverse_setting['extend-g'] == 'none':
                r_max_g = str(system['r_max_u'])
            elif inverse_setting['extend-g'] == 'extrapolate':
                r_max_g = str(system['r_max_u'])
            elif inverse_setting['extend-g'] == 'sample':
                r_max_g = str(system['r_extend_g'])
            else:
                raise NotImplementedError
        #print(f"r_max_g: {r_max_g}")
        for ele in root.findall('non-bonded'):
            ele.find('max').text = r_max_g
            if 'non-bonded-post-add' in inverse_setting['method']:
                ele.find('inverse').find('post_add').text = ' '.join(inverse_setting['method']['non-bonded-post-add'])
        # bonded potential settings
        for ele in root.findall('bonded'):
            if inverse_setting.get('intra-treat') == 'fix':
                ele.find('inverse').find('do_potential').text = '0'
            elif inverse_setting.get('intra-treat') == 'ibi':
                # (IBI with votca for angles and dihredrals and rings work only with scaling factors in settings)
                ele.find('inverse').find('do_potential').text = '1'
        # imc settings
        if inverse_setting['method']['method'] == 'imc':
            imc = ET.SubElement(root.find('inverse'), 'imc')
            default_reg = ET.SubElement(imc, 'default_reg')
            default_reg.text = str(inverse_setting['method']['regul'])
            if 'has_intra' in system['tags']:
                bonded_method = ET.SubElement(imc, 'bonded_method')
                bonded_method.text = inverse_setting['intra-treat']
                if inverse_setting['intra-treat'] == 'ibi':
                    settings_nonbonded = ET.SubElement(imc, 'settings_nonbonded')
                    settings_nonbonded.text = 'settings-nonbonded.xml'
                    # add topology.xml and settings-nonbonded.xml to filelist
                    filelist = root.find('inverse').find('filelist')
                    filelist.text = filelist.text + ' topology.xml settings-nonbonded.xml'
        # iie settings
        if inverse_setting['method']['method'] == 'iie':
            iie = ET.SubElement(root.find('inverse'), 'iie')
            iie_method = ET.SubElement(iie, 'method')
            iie_method.text = inverse_setting['method']['algorithm']
            iie_closure = ET.SubElement(iie, 'closure')
            iie_closure.text = inverse_setting['method']['closure']
            if 'has_intra' in system['tags']:
                ignore_intra = ET.SubElement(iie, 'ignore_intramolecular_correlation')
                ignore_intra.text = str(inverse_setting['method']['ignore-intra'])
            # initial guess settings
            initial_guess = ET.SubElement(iie, 'initial_guess')
            initial_guess_method = ET.SubElement(initial_guess, 'method')
            initial_guess_method.text = inverse_setting['init']['method']
            if initial_guess_method.text == 'ie':
                initial_guess_closure = ET.SubElement(initial_guess, 'closure')
                initial_guess_closure.text = inverse_setting['init']['closure']
                if 'has_intra' in system['tags']:
                    initial_guess_ignore_intra = ET.SubElement(initial_guess, 'ignore_intramolecular_correlation')
                    initial_guess_ignore_intra.text = str(inverse_setting['init']['ignore-intra'])
            densities = ET.SubElement(iie, 'densities')
            densities.text = str(system['top'].nmols() / system['volume'])
            n_intra = ET.SubElement(iie, 'n_intra')
            n_intra.text = ' '.join((str(len(moltype['cg_repr'])) for moltype in system['moltypes']))
            cut_off = ET.SubElement(iie, 'cut_off')
            cut_off.text = str(system['r_max_u'])
            if inverse_setting['extend-g'] == 'extrapolate':
                g_extrap_factor = ET.SubElement(iie, 'g_extrap_factor')
                g_extrap_factor.text = str(system['r_extend_g'] / system['r_max_u'])
            if inverse_setting.get('extrap_near_core'):
                raise NotImplementedError
            if inverse_setting.get('fix_near_cut_off'):
                raise NotImplementedError
            if inverse_setting['method']['algorithm'] == 'gauss-newton':
                cut_gn = system['r_max_u'] * inverse_setting['method']['gn-ranges'][0]
                print(f"cut_gn: {cut_gn}")
                cut_gn_xml = ET.SubElement(iie, 'cut_gn')
                cut_gn_xml.text = str(cut_gn)
            if 'cut-jacobian' in inverse_setting:
                cut_jacobian = ET.SubElement(iie, 'cut_jacobian')
                cut_jacobian.text = str(inverse_setting['cut-jacobian'])
        # write xml
        indent(root)
        tree.write('settings.xml')
        
        # cut offs
        for tag in ('rlist', 'rcoulomb', 'rvdw'):
            gt.mdp.set_parameter("grompp.mdp", tag, system['r_max_u'])
        # run length
        if inverse_setting['method']['method'] == 'imc':
            gt.mdp.set_parameter("grompp.mdp", 'nsteps', 310000)
        else:
            gt.mdp.set_parameter("grompp.mdp", 'nsteps',  70000)
        # set temperature
        gt.mdp.set_parameter("grompp.mdp", 'ref-t', system['temperature'])
        # make index file
        if system['type'] in ('hexane', 'hexane-longer-rdf'):
            run_bash(f"gmx make_ndx -f conf.gro -o index.ndx << EOF\na A1 A2\nname 3 A\nq\nEOF")
        elif system['type'] in ('naphtalene', 'naphtalene-longer-rdf'):
            run_bash(f"gmx make_ndx -f conf.gro -o index.ndx << EOF\na A1 A2 A3 A4\nname 3 A\nq\nEOF")
        else:
            run_bash(f"gmx make_ndx -f conf.gro -o index.ndx << EOF\na A\nq\nEOF")
        run_bash(f"rm -f \#*")

        # consistent pot.in for all hncinit methods, since otherwise it depends on lenght of g_tgt
        if inverse_setting['init']['method'] == 'table':
            interaction_name = 'A-A'
            # copy to .pot.in
            run_bash(f"cp {interaction_name}{inverse_setting['init']['table']} {interaction_name}.pot.in")
        elif inverse_setting['init']['method'] == 'bi':
            # this will be chosen automatically
            pass
        else:
            raise Exception(str(inverse_setting['init']['method']) + " not implemented here!")
        # imc-ibiintra generate settings-nonbonded.xml
        if inverse_setting['method']['method'] == 'imc' and 'has_intra' in system['tags']:
            if inverse_setting['intra-treat'] == 'ibi':
                # generate settings-nonbonded.xml
                run_bash(f"cp settings.xml settings-nonbonded.xml")
                tree = ET.parse('settings-nonbonded.xml')
                root = tree.getroot()
                for child in root.findall("bonded"):
                    root.remove(child)
                tree.write('settings-nonbonded.xml')

## run inverse

In [ ]:
for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_cg, inverse_settings_for_cg):
    print(working_dir)
    remote_dir = os.path.join(remote_dir_base, system['name'], inverse_setting['name'])
    
    with WorkingDir(working_dir):
        # mkdir
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")
        
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")
        
        # copy simulation files to remote
        filelist = [
            "settings.xml",
            "*.dist*.tgt",
            "table*.xvg",
            "grompp.mdp",
            "conf.gro",
            "topol.top",
            "index.ndx",
            "topology.xml",
        ]
        if inverse_setting['init']['method'] in ('table',):
            filelist += [
                "*.pot.in",
            ]
        if 'has_intra' in system['tags']:
            filelist += [
                "map.xml",
            ]
            if inverse_setting['method']['method'] == 'imc' and inverse_setting['intra-treat'] == 'ibi':
                filelist += [
                    "settings-nonbonded.xml",
                ]
            
        gt.remote.push_files(filelist, remote_host, remote_dir, exclude="step_*")
        
        # commands to be run on compute nodes
        script = remote_header + """
ln -sf $JOBTMP jobtmp
csg_inverse --options settings.xml
unlink jobtmp
""" + remote_footer

        jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
        print(jobid)
        if jobid != None:
            jobids.append(jobid)

## check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

## copy results from cluster

In [ ]:
# WARNING, do not interupt these, sometimes leeds to local empty directorys
for (s,i), (system, inverse_setting, working_dir) in iterator_sys_inv(systems_to_cg, inverse_settings_for_cg, return_indices=True):
    print(working_dir)
    remote_dir = os.path.join(remote_dir_base, system['name'], inverse_setting['name'])
    
    with WorkingDir(working_dir):
        filelist = ["step_*/*.dist*.new", "step_*/*.pot.new", "step_*/*.dpot.new",
                   "step_001/*.pot.cur", "step_001/table_A_A.xvg",
                   "step_001/*.dist.tgt",
                   "step_001/*.npz",
                   "step_001/*.gmc",
                   "step_*/ener.edr", "step_000/*.dist.tgt", "step_*/done"]
        exclude = "*traj*"
        try:
            gt.remote.pull_files(filelist, remote_host, remote_dir, exclude=exclude)
        except:
            print(f'no data on {remote_host}!')

# Analysis and plots

## systems and methods of interest

In [ ]:
systems_to_show = []
systems_to_show += [system for system in systems if system['name'] in [
    #'lj/near-critical',
    'lj/near-triple',
    #'spce',
    #'hexane',
    #'naphtalene',
]]

inverse_settings_to_show = []
inverse_settings_to_show += [invset for invset in inverse_settings if invset['name'] in [
    'ibi-hncinit-ibiintra',
    'imc0.3-hncinit-ibiintra',
    'hncn-hncinit-ibiintra',
    'hncned-hncinit-ibiintra',
    'hncnedf-hncinit-ibiintra',
    'hncnex-hncinit-ibiintra',
    'hncgned-hncinit-ibiintra',
    'hncgn-1.5-2-hncinit-ibiintra',
    'hncgn-2-2-hncinit-ibiintra',
    'hncgn-1.05-2-hncinit-ibiintra',
    'ibi-biinit-ibiintra',
]]

comparisons_to_show = []
#comparisons_to_show += ['ihncii-hncinit-ibiintra/step_010']

In [ ]:
for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_show, inverse_settings_to_show):
    print(working_dir)

## equilibration check

In [ ]:
# pressure from RDF and U
# force from average of forward and backward derivative of U
def calc_pressure_bar1(r, g, U, rho, kBT, cut_off, g_min):
    delta_r = r[1] - r[0]
    core_end = np.where(g > g_min)[0][0]
    cut_off = np.searchsorted(r, cut_off)
    main = slice(core_end, cut_off+2)
    uprime1 = np.concatenate((np.diff(U[main]), [0])) / delta_r
    uprime2 = np.concatenate(([0], np.diff(U[main]))) / delta_r
    uprime = (uprime1 + uprime2) / 2
    #uprime = uprime1
    p_rdf = rho*kBT - 2/3 * np.pi * rho**2 * delta_r * np.sum(uprime * g[main] * r[main]**3)
    return p_rdf * 1e28 * const.u  # conversion from md units to bar

# read votca table
def readin_table(filename):
    table_dtype = {'names': ('x', 'y', 'y_flag'),
                   'formats': ('f', 'f', 'S1')}
    x, y, y_flag = np.loadtxt(filename, dtype=table_dtype, comments=['#', '@'], unpack=True)
    return x, y, y_flag

In [ ]:
cmap = plt.get_cmap('rainbow')

for system in systems_to_show:
    print("system", system['name'])
    
    # find target pressure
    tmp_fd, tmp_path = tempfile.mkstemp(suffix='.xvg')
    try:
        run_bash(f"gmx -quiet energy -f {system['name']}/fine-grained/prod/ener.edr -o {tmp_path} <<< 'pressure'")
        pressure, _ = gt.xvg.load(tmp_path)
        pressure_target = pressure['Pressure'].mean()
    finally:
        os.remove(tmp_path)
        
    # show stuff
    for inverse_setting in (inverse_setting for inverse_setting in inverse_settings_to_show
                            if system['type'] in inverse_setting['system-types']):
        print("inverse_setting", inverse_setting['name'])
        
        working_dir = os.path.join(working_dir_base, system['name'], inverse_setting['name'])
        with WorkingDir(working_dir):
            ener_files = sorted(glob.glob('step_*/ener.edr'))
            if ener_files == []:
                print('.. nothing here ..')
                continue
            max_step = int(re.search('step_(\d+)', ener_files[-1]).group(1))
            steps = []
            pressures = []
            pressures_std = []
            
            # energy files to actually plot
            ener_files_to_show = ener_files
            #ener_files_to_show = ener_files[-10:]
            # reduce to ten energy lines
            if len(ener_files_to_show) > 5:
                ener_files_to_show = ener_files_to_show[::len(ener_files_to_show)//5]
            
            fig, (ax0, ax1, ax2) = plt.subplots(nrows=1, ncols=3, figsize=[18, 2])
            # load data and plot
            for ener_file in ener_files:
                # skip empty ener.edr
                if os.stat(ener_file).st_size == 0:
                    continue
                # get step int
                step = int(re.search('step_(\d+)', ener_file).group(1))
                steps.append(step)
                # get energy data
                tmp_fd, tmp_path = tempfile.mkstemp(suffix='.xvg')
                try:
                    run_bash(f"gmx energy -f {ener_file} -o {tmp_path} <<< 'Temperature\nPressure'")
                    data, _ = gt.xvg.load(tmp_path)
                finally:
                    os.remove(tmp_path)
                pressures.append(data[data['Time (ps)'] > 10]['Pressure'].mean())
                pressures_std.append(data[data['Time (ps)'] > 10]['Pressure'].std())
                
                if ener_file in ener_files_to_show:
                    ax0.plot(data['Time (ps)'], np.array(data['Temperature']), label=step, color=cmap(step/max_step))
                    ax1.plot(data['Time (ps)'], np.array(data['Pressure']), label=step, color=cmap(step/max_step))
            
            # plot average pressure
            ax2.errorbar(steps, pressures, pressures_std, label='pressure cur')
            # plot target pressure
            ax2.axhline(pressure_target, linestyle=':', label='pressure tgt')
            #ax2.set_ylim((-2*pressure_target, 8*pressure_target))
            
            # calculate virial pressures
            pressures_vir = []
            for step in steps:
                pot_file = f"step_{step:03d}/A-A.pot.cur"
                rdf_file = f"step_{step:03d}/A-A.dist.new"
                if (not os.path.exists(pot_file)) or (not os.path.exists(rdf_file)):
                    pressures_vir.append(None)
                    continue
                r, U, _ = readin_table(pot_file)
                r, g, _ = readin_table(rdf_file)
                density = system['top'].nmols() / system['volume']
                kBT = oconst.k_gro * system['temperature']
                #pressure_vir = calc_pressure_bar1(r, g, U, density, kBT, system['r_max_u'], 1e-10)
                #pressures_vir.append(pressure_vir)
            #ax2.plot(steps, pressures_vir, label='virial cur')
                 

        ax0.set_title("Temperature")
        ax1.set_title("Pressure")
        ax2.set_title("Pressure vs. step")
        ax2.set_xlabel('step')
        ax2.set_ylabel('pressure in bar')
        ax2.xaxis.set_major_locator(mpl.ticker.MaxNLocator(integer=True))
        ax0.legend(loc='center right')
        ax2.legend()
        fig.tight_layout()    
        fig.savefig(os.path.join(working_dir_base, "figures", f"p-convergence_{inverse_setting['name']}_{system['name'].replace('/', '-')}.png"), dpi=150)
        plt.show()

## show initial guess and its RDF fit

In [ ]:
with mpl.rc_context(rc={'figure.dpi': 100}):
    for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_show, inverse_settings_to_show):
        print(working_dir)
        with WorkingDir(working_dir):
            
            try:
                data = np.loadtxt("step_000/A-A.pot.new", dtype=np.str, comments=['#', '@'])
                data_tgt = np.loadtxt("A-A.dist.tgt", dtype=np.str, comments=['#', '@'])
                data_1 = np.loadtxt("step_001/A-A.dist.new", dtype=np.str, comments=['#', '@'])
            except:
                print(':: could not load all needed files ::')
                continue
                
            fig, axes = plt.subplots(1, 2, figsize=(6, 2))
            
            r = data[:, 0].astype(np.float)
            U = data[:, 1].astype(np.float)
            ax = axes[0]
            ax.plot(r, U)
            ax.set_xlim(0, system['r_max_u'])
            ax.set_ylim(-3, 3)
            ax.set_ylim(min(U)-0.5, 3)
            ax.set_xlabel("r / nm")
            ax.set_ylabel("U")
            
            r_tgt = data_tgt[:, 0].astype(np.float)
            g_tgt = data_tgt[:, 1].astype(np.float)
            r_1 = data_1[:, 0].astype(np.float)
            g_1 = data_1[:, 1].astype(np.float)
            #print(f'sqrt((g-g_tgt)²): {np.sqrt(np.trapz(x=r_1, y=(g_1 - g_tgt)**2)):.3f}')
            ax = axes[1]
            ax.plot(r_1, g_1, label='step 0')
            ax.plot(r_tgt, g_tgt, 'k:', label='target')
            ax.set_xlim(0, system['r_extend_g'])
            ax.set_ylim(0)
            ax.set_xlabel("r / nm")
            ax.set_ylabel("g")
            ax.legend()
            ax.grid()
            #ax.vlines(system['r_max_g'], 0.1, 0.9, linestyles='--')
            #ax.vlines(system['r_max_u'], 0.1, 0.9, linestyles=':')
            fig.tight_layout()
            fig.savefig(os.path.join(working_dir_base, "figures", f"initial-guess_{inverse_setting['name']}_{system['name'].replace('/', '-')}.png"), dpi=300)
            plt.show()

## initial guess paper figure

In [ ]:
paper_method_plots = {
    'hncinit': {
        'sys-inv-to-plot': [
            [
                (systems_dict['spce'], invsets_dict['ibi-biinit-ibiintra']),
                (systems_dict['spce'], invsets_dict['ibi-hncinit-ibiintra']),
            ], [
                (systems_dict['hexane'], invsets_dict['ibi-biinit-ibiintra']),
                (systems_dict['hexane'], invsets_dict['ibi-hncinit-ibiintra']),
            ], [
                (systems_dict['naphtalene'], invsets_dict['ibi-biinit-ibiintra']),
                (systems_dict['naphtalene'], invsets_dict['ibi-hncinit-ibiintra']),
            ]
        ],
    },
}

system_short_names = {
    'spce': 'water'
}

In [ ]:
from cycler import cycler
cmap = plt.get_cmap('rainbow')

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    'axes.prop_cycle': (
        cycler(color=['#EDAE49', '#00798C'])
        + cycler(ls=['--', ':'])
    ),

}

with mpl.rc_context(rc=mpl_rc):
    for paper_method_plot_name, paper_method_plot in paper_method_plots.items():
    
        fig, axes = plt.subplots(nrows=2, ncols=len(paper_method_plot['sys-inv-to-plot']), figsize=[4.77, 3],
                                squeeze=False, sharex='col', sharey='row')
        #axes[0,1].get_shared_y_axes().join(axes[0,1], axes[0,2])

        legend_lines = []
        for s, sys_inv_column in enumerate(paper_method_plot['sys-inv-to-plot']):
            # once per system
            ax0 = axes[0, s]
            ax1 = axes[1, s]

            for i, (system, inverse_setting) in enumerate(sys_inv_column):
                print(s, i, system['name'], inverse_setting['name'])
                working_dir = system['name'] + '/' + inverse_setting['name']
                working_dir_parent = os.path.join(working_dir_base, system['name'])

                with WorkingDir(working_dir):
                    interaction_name = 'A-A'
                    # plot initial guess
                    pot_r, pot_U, pot_flag = readin_table('step_000/A-A.pot.new')
                    line_u, = ax0.plot(pot_r, pot_U)
                    # plot target
                    if i == 0:
                        dist_tgt_r, dist_tgt_g, _ = readin_table(f"{interaction_name}.dist.tgt")
                        line_tgt, = ax1.plot(dist_tgt_r, dist_tgt_g, color='k', linestyle='-')
                    # plot rdf
                    dist_r, dist_g, dist_flag = readin_table('step_001/A-A.dist.new')
                    line_g, = ax1.plot(dist_r, dist_g)
                    # legend lines
                    if s == 0:
                        if i == 0:
                            legend_lines.append((line_tgt, 'target'))
                        label = {'bi': 'BI', 'table': 'HNC'}[inverse_setting['init']['method']]
                        legend_lines.append((line_g, label))

            # first column
            if s == 0:
                ax0.set_ylabel(r"$u(r)$ in kJ mol¯¹", labelpad=-1)
                ax1.set_ylabel(r"$g(r)$")
                ax0.set_ylim((-3.0, 4.0))
            # last column
            ax0.set_xlim(system['r_max_u'] * np.array([0.29, 1.01]))
            ax1.set_ylim((0, 4.2))
            ax1.set_xlabel(r"$r$ in nm")

            # remove last tick
            ax1.yaxis.get_major_ticks()[-1].label1.set_visible(False)

            ax0.set_title(system_short_names.get(system['type'], system['type']))

        fig.legend(*zip(*legend_lines), loc=(0.45, 0.32), ncol=1)
        fig.tight_layout()    
        plt.subplots_adjust(hspace=0.0, wspace=0.0)
        fig.savefig(os.path.join(working_dir_base, "figures", f"init-comparison.pdf"))
        plt.show()

In [ ]:
run_bash("cp figures/init-comparison.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

## dist, dU, U

In [ ]:
def readin_table(filename):
    data = np.loadtxt(filename, dtype=np.str, comments=['#', '@'])
    x = data[:, 0].astype(np.float)
    y = data[:, 1].astype(np.float)
    y_flag = data[:, 2].astype('S1')
    return x, y, y_flag

In [ ]:
cmap = plt.get_cmap('rainbow')

mpl_rc = {
    'figure.dpi': 100,
    'legend.title_fontsize': 8,
    'legend.fontsize': 8,
    'legend.handlelength': 1,
}

with mpl.rc_context(rc=mpl_rc):
    for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_show, inverse_settings_to_show):
        print(working_dir)
        working_dir_parent = os.path.join(working_dir_base, system['name'])
        with WorkingDir(working_dir):
            if len(glob.glob('step_*/')) <= 1:
                print('.. nothing here ..')
                continue
                
            fig, (ax0, ax1, ax2) = plt.subplots(nrows=1, ncols=3, figsize=[10, 3])

            # plot g(r) or Δg(r)
            plot_delta_g = False
            dist_files = sorted(glob.glob('step_*/A-A.dist.new'))
            #dist_files = dist_files[::max(max_step//8, 1)]
            #dist_files = dist_files[:5] + dist_files[-1:]
            #dist_files = dist_files[:10]
            axins0 = inset_axes(ax0, width="70%", height="40%", loc='upper right')
            # load target g(r)
            dist_tgt_r, dist_tgt_g, _ = readin_table("A-A.dist.tgt")
            g_std = []
            for i, dist_file in enumerate(dist_files):
                step = int(re.search('step_(\d+)', dist_file).group(1))
                dist_r, dist_g, dist_flag = readin_table(dist_file)
                noextend = slice(0, len(dist_r))
                if plot_delta_g:
                    ax0.plot(dist_r, dist_g - dist_tgt_g[noextend], label=f"{step}", color=cmap(i/len(dist_files)))
                else:
                    ax0.plot(dist_r, dist_g, label=f"{step}", color=cmap(i/len(dist_files)))
                ax0.set_title(r'$Δg(r)$' if plot_delta_g else r'$g(r)$')
                
                distance = dist_g[noextend] - dist_tgt_g[noextend]
                norm_r = dist_r[noextend]
                g_std.append((step, np.sqrt(np.trapz(x=norm_r, y=distance**2))))
                
            # plot target g(r)
            if plot_delta_g:
                ax0.plot(dist_r, np.zeros_like(dist_r), label=f"tgt", color='k', linestyle='--')
                ax0.set_ylim(-0.04, 0.02)
            else:
                ax0.plot(dist_tgt_r, dist_tgt_g, label="tgt", color='k', linestyle='--')
                
            # now that we have g, define core_end
            ndx_ce = np.where(dist_g > 1e-10)[0][0]
            core_end = dist_r[ndx_ce]
                
            axins0.plot(*zip(*g_std))
            axins0.set_ylim(0, 0.02)
            axins0.grid()
            #axins0.remove()

            # plot dU(r)  
            dpot_files = sorted(glob.glob('step_*/A-A.dpot.new'))
            #dpot_files = dpot_files[::max(max_step//8, 1)]
            #dpot_files = dpot_files[:5] + dpot_files[-2:]
            #dpot_files = dpot_files[:10]
            for i, dpot_file in enumerate(dpot_files):
                step = int(re.search('step_(\d+)', dpot_file).group(1))
                dpot_r, dpot_dU, dist_flag = readin_table(dpot_file)
                ax1.plot(dpot_r, dpot_dU, '.-', label=f"{step}", color=cmap(i/len(dpot_files)))
                #ax1.plot([0.88, 0.88], [-100, 100], '--')
                #print(dpot_r[40:50])
                #print(dpot_dU[40:50])
                ax1.set_title("ΔU(r)")
                ax1.set_ylim((-0.1, 0.1))
                #ax1.set_ylim((-50, 50))
                #ax1.set_ylim((-100, 100))

            # plot U(r)
            pot_files = sorted(glob.glob('step_*/A-A.pot.new'))
            #pot_files = pot_files[::max(max_step//8, 1)]
            #pot_files = pot_files[:5] + pot_files[-1:]
            #pot_files = pot_files[:10]
            axins2 = inset_axes(ax2, width="20%", height="40%", loc='upper center')
            for i, pot_file in enumerate(pot_files):
                step = int(re.search('step_(\d+)', pot_file).group(1))
                pot_r, pot_U, dist_flag = readin_table(pot_file)
                ax2.plot(pot_r, pot_U, label=f"{step}", color=cmap(i/len(pot_files)))
                axins2.plot(pot_r, pot_U, '.-', label=f"{step}", color=cmap(i/len(pot_files)))
                #ax2.set_ylim((-1.3, 3))
                ax2.set_ylim((-1.1, 1.1))
                #ax2.set_ylim((-20, 100))
                ax2.set_title("U(r)")

            cut_off = system['r_max_u']
            #axins2.set_xlim(0.9*core_end, 1.15*core_end)
            axins2.set_xlim(0.97*cut_off, 1.01*cut_off)
            #axins2.set_ylim(pot_U[ndx_ce]-30, pot_U[ndx_ce]+0)
            axins2.set_ylim(-0.03, 0.03)
            axins2.remove()

            # plot target U(r)
            if system['type'] == 'lj':
                tgt_r = dist_r[1:]
                pot_target = 4 * ((1/tgt_r)**12 - (1/tgt_r)**6)
                ax2.plot(tgt_r, pot_target, label="tgt", color='k', linestyle='--')
                axins2.plot(tgt_r, pot_target, label="tgt", color='k', linestyle='--')

            # plot comparisons
            for comparison in comparisons_to_show:
                with WorkingDir(working_dir_parent):
                    pot_r, pot_U, pot_flag = readin_table(f"{comparison}/A-A.pot.new")
                ax2.plot(pot_r, pot_U, linestyle='--', color='k', label='c.')  # label=comparison.split('/')[0])

            #ax0.legend(loc='upper right', title='step')
            #ax1.legend(loc='upper left', title='step')
            #ax2.legend(loc='upper left', title='step')
            #ax2.grid()
            for ax in (ax0, ax1, ax2):
                ax.set_xlim((0.0, system['r_max_u'] + 0.0))
                ax.set_xlabel("r in nm")
                #ax.grid()
            for ax in (ax1, ax2):
                ax.set_ylabel("U in kJ mol¯¹")

            #ax0.set_xlim((0.8*g_start, 1.2*g_start))
            #ax1.set_xlim((0.8*g_start, 1.2*g_start))
            #ax2.set_xlim((0.8*g_start, 1.2*g_start))
            ax0.set_xlim((0.0, system['r_max_u'] + 0.0))
            #ax2.set_xlim((0.5, 0.7))
            #ax2.set_ylim((-1.0, -0.5))

        #fig.tight_layout()    
        fig.savefig(os.path.join(working_dir_base, "figures", f"{inverse_setting['name']}_{system['name'].replace('/', '-')}.png"), dpi=300)
        plt.show()

## dist, dU, U (bond)

In [ ]:
cmap = plt.get_cmap('rainbow')

mpl_rc = {
    'figure.dpi': 100,
    'legend.title_fontsize': 8,
    'legend.fontsize': 8,
    'legend.handlelength': 1,
}

with mpl.rc_context(rc=mpl_rc):
    for system, inverse_setting, working_dir in iterator_sys_inv(systems_to_show, inverse_settings_to_show):
        print(working_dir)
        working_dir_parent = os.path.join(working_dir_base, system['name'])
        with WorkingDir(working_dir):
            if len(glob.glob('step_*/')) <= 1:
                print('.. nothing here ..')
                continue
            if not 'has_intra' in system['tags']:
                print('.. no intra ..')
                continue
                
            tree_map = ET.parse('map.xml')
            cg_bondeds = tree_map.find('topology').find('cg_bonded').findall('*')
            for cg_bonded in cg_bondeds:
                interaction_type = cg_bonded.tag
                interaction_name = cg_bonded.find('name').text
                print(interaction_type, interaction_name)
                
                fig, (ax0, ax1, ax2) = plt.subplots(nrows=1, ncols=3, figsize=[10, 3])

                # plot g(r) or Δg(r)
                plot_delta_g = False
                dist_files = sorted(glob.glob(f'step_*/{interaction_name}.dist.new'))
                #dist_files = dist_files[::max(max_step//8, 1)]
                #dist_files = dist_files[:5] + dist_files[-1:]
                dist_files = dist_files[:10]
                axins0 = inset_axes(ax0, width="70%", height="40%", loc='lower center')
                # load target g(r)
                _, dist_tgt_g, _ = readin_table(f"{interaction_name}.dist.tgt")
                g_std = []
                for i, dist_file in enumerate(dist_files):
                    step = int(re.search('step_(\d+)', dist_file).group(1))
                    dist_r, dist_g, dist_flag = readin_table(dist_file)
                    if plot_delta_g:
                        ax0.plot(dist_r, dist_g - dist_tgt_g, label=f"{step}", color=cmap(i/len(dist_files)))
                    else:
                        ax0.plot(dist_r, dist_g, label=f"{step}", color=cmap(i/len(dist_files)))
                    ax0.set_title(r'$Δp(r)$' if plot_delta_g else r'$p(r)$')

                    g_std.append((step, np.sqrt(np.trapz(x=dist_r, y=(dist_g - dist_tgt_g)**2))))

                # plot target g(r)
                if plot_delta_g:
                    ax0.plot(dist_r, np.zeros_like(dist_r), label=f"tgt", color='k', linestyle='--')
                    #ax0.set_ylim(-0.04, 0.02)
                else:
                    ax0.plot(dist_r, dist_tgt_g, label="tgt", color='k', linestyle='--')

                # now that we have g, define core_end
                ndx_ce = np.where(dist_g > 1e-10)[0][0]
                core_end = dist_r[ndx_ce]

                axins0.plot(*zip(*g_std))
                #axins0.set_ylim(0, 0.02)
                axins0.grid()
                axins0.remove()

                # plot dU(r)  
                dpot_files = sorted(glob.glob(f'step_*/{interaction_name}.dpot.new'))
                #dpot_files = dpot_files[::max(max_step//8, 1)]
                #dpot_files = dpot_files[:5] + dpot_files[-2:]
                dpot_files = dpot_files[:10]
                for i, dpot_file in enumerate(dpot_files):
                    step = int(re.search('step_(\d+)', dpot_file).group(1))
                    dpot_r, dpot_dU, dist_flag = readin_table(dpot_file)
                    ax1.plot(dpot_r, dpot_dU, '.-', label=f"{step}", color=cmap(i/len(dpot_files)))
                    #ax1.plot([0.88, 0.88], [-100, 100], '--')
                    #print(dpot_r[40:50])
                    #print(dpot_dU[40:50])
                    ax1.set_title("ΔU(r)")
                    #ax1.set_ylim((-50, 50))
                    #ax1.set_ylim((-100, 100))

                # plot U(r)
                pot_files = sorted(glob.glob(f'step_*/{interaction_name}.pot.new'))
                #pot_files = pot_files[::max(max_step//8, 1)]
                #pot_files = pot_files[:5] + pot_files[-1:]
                pot_files = pot_files[:10]
                axins2 = inset_axes(ax2, width="20%", height="40%", loc='upper center')
                for i, pot_file in enumerate(pot_files):
                    step = int(re.search('step_(\d+)', pot_file).group(1))
                    pot_r, pot_U, dist_flag = readin_table(pot_file)
                    ax2.plot(pot_r, pot_U, label=f"{step}", color=cmap(i/len(pot_files)))
                    axins2.plot(pot_r, pot_U, '.-', label=f"{step}", color=cmap(i/len(pot_files)))
                    ax2.set_ylim((0, 10))
                    #ax2.set_ylim((-20, 100))
                    ax2.set_title("U(r)")

                cut_off = system['r_max_u']
                #axins2.set_xlim(0.9*core_end, 1.15*core_end)
                #axins2.set_xlim(0.97*cut_off, 1.01*cut_off)
                #axins2.set_ylim(pot_U[ndx_ce]-30, pot_U[ndx_ce]+0)
                #axins2.set_ylim(-0.03, 0.03)
                axins2.remove()

                # plot target U(r)
                if system['type'] == 'lj':
                    tgt_r = dist_r[1:]
                    pot_target = 4 * ((1/tgt_r)**12 - (1/tgt_r)**6)
                    ax2.plot(tgt_r, pot_target, label="tgt", color='k', linestyle='--')
                    axins2.plot(tgt_r, pot_target, label="tgt", color='k', linestyle='--')

                ax0.legend(loc='upper left', title='step')
                ax1.legend(loc='upper left', title='step')
                ax2.legend(loc='upper left', title='step')
                #ax2.grid()
                for ax in (ax0, ax1, ax2):
                    #ax.set_xlim((0.0, system['r_max_u'] + 0.2))
                    ax.set_xlabel("r in nm")
                    #ax.grid()
                for ax in (ax1, ax2):
                    ax.set_ylabel("U in kJ mol¯¹")

                #ax0.set_xlim((0.8*g_start, 1.2*g_start))
                #ax1.set_xlim((0.8*g_start, 1.2*g_start))
                #ax2.set_xlim((0.8*g_start, 1.2*g_start))
                #ax0.set_ylim((0.0, 1.5))

                fig.tight_layout()    
                #fig.savefig(os.path.join(working_dir_base, "figures", f"{inverse_setting['name']}_{system['name'].replace('/', '-')}.png"), dpi=300)
                plt.show()

## method comparison plot for paper

- 6 subplots (2 rows, 3 columns)
- in rows potential, rdf
- in columns water, hexane, naphtalene
- each subplot has a subfigure with the convergence
- potential convergence from sqrt((g * dU)^2) ? 

In [ ]:
paper_method_plots = {
    'hncinit': {
        'sys-inv-to-plot': [
            [
                (systems_dict['lj/near-triple'], invsets_dict['ibi-hncinit-ibiintra']),
                (systems_dict['lj/near-triple'], invsets_dict['imc0.3-hncinit-ibiintra']),
                #(systems_dict['lj/near-triple'], invsets_dict['hncn-hncinit-ibiintra']),
                (systems_dict['lj/near-triple'], invsets_dict['hncnedf-hncinit-ibiintra']),
                (systems_dict['lj/near-triple'], invsets_dict['hncned-hncinit-ibiintra']),
                (systems_dict['lj/near-triple'], invsets_dict['hncnex-hncinit-ibiintra']),
                (systems_dict['lj/near-triple'], invsets_dict['hncgned-hncinit-ibiintra']),
            ], [
                (systems_dict['spce'], invsets_dict['ibi-hncinit-ibiintra']),
                (systems_dict['spce'], invsets_dict['imc0.3-hncinit-ibiintra']),
                #(systems_dict['spce'], invsets_dict['hncn-hncinit-ibiintra']),
                (systems_dict['spce'], invsets_dict['hncnedf-hncinit-ibiintra']),
                (systems_dict['spce'], invsets_dict['hncned-hncinit-ibiintra']),
                (systems_dict['spce'], invsets_dict['hncnex-hncinit-ibiintra']),
                (systems_dict['spce'], invsets_dict['hncgned-hncinit-ibiintra']),
            ], [
                (systems_dict['hexane'], invsets_dict['ibi-hncinit-ibiintra']),
                (systems_dict['hexane'], invsets_dict['imc0.3-hncinit-ibiintra']),
                #(systems_dict['hexane'], invsets_dict['hncn-hncinit-ibiintra']),
                (systems_dict['hexane'], invsets_dict['hncnedf-hncinit-ibiintra']),
                (systems_dict['hexane'], invsets_dict['hncned-hncinit-ibiintra']),
                (systems_dict['hexane'], invsets_dict['hncnex-hncinit-ibiintra']),
                (systems_dict['hexane'], invsets_dict['hncgned-hncinit-ibiintra']),
            ], [
                (systems_dict['naphtalene'], invsets_dict['ibi-hncinit-ibiintra']),
                (systems_dict['naphtalene'], invsets_dict['imc0.3-hncinit-ibiintra']),
                #(systems_dict['naphtalene'], invsets_dict['hncn-hncinit-ibiintra']),
                (systems_dict['naphtalene'], invsets_dict['hncnedf-hncinit-ibiintra']),
                (systems_dict['naphtalene'], invsets_dict['hncned-hncinit-ibiintra']),
                (systems_dict['naphtalene'], invsets_dict['hncnex-hncinit-ibiintra']),
                (systems_dict['naphtalene'], invsets_dict['hncgned-hncinit-ibiintra']),
            ]
        ],
    },
}
system_short_names = {'spce': 'water'}

In [ ]:
from cycler import cycler

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 120,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    'axes.prop_cycle': (
        cycler(color=['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B', '#22ad5a'])
        + cycler(ls=['-', '--', ':', (0, (5, 1)), '-.', '--'])
    ),

}

with mpl.rc_context(rc=mpl_rc):
    for paper_method_plot_name, paper_method_plot in paper_method_plots.items():
    
        fig, axes = plt.subplots(nrows=2, ncols=len(paper_method_plot['sys-inv-to-plot']), figsize=[4.77, 3],
                                squeeze=False, sharex='col', sharey='row')

        legend_lines = []
        for s, sys_inv_column in enumerate(paper_method_plot['sys-inv-to-plot']):
            # once per system
            ax0 = axes[(0,s)]
            ax1 = axes[(1,s)]
            #axins0 = inset_axes(ax0, width="50%", height="40%", loc='upper right')
            axins1 = inset_axes(ax1, width="50%", height="40%", loc='upper right')

            for i, (system, inverse_setting) in enumerate(sys_inv_column):
                print(s, i, system['name'], inverse_setting['name'])
                working_dir = system['name'] + '/' + inverse_setting['name']
                working_dir_parent = os.path.join(working_dir_base, system['name'])

                with WorkingDir(working_dir):
                    interaction_name = 'A-A'
                    """
                    # plot initial guess
                    try:
                        pot_r, pot_U, pot_flag = readin_table('step_000/A-A.pot.new')
                        ax0.plot(pot_r, pot_U, '-.', color='darkgreen', label='initial guess')
                    except:
                        print('.. no data ..', system['name'], inverse_setting['name'])
                    """
                    # plot potential
                    try:
                        pot_r, pot_U, pot_flag = readin_table('step_019/A-A.pot.new')
                        ax0.plot(pot_r, pot_U, label=inverse_setting['name'])
                    except:
                        print('.. no potential data ..', system['name'], inverse_setting['name'])
                        ax0.plot([], [], label=inverse_setting['name'])
                    # gather potential convergence data
                    try:
                        dU_std = []
                        dpot_files = sorted(glob.glob(f'step_*/{interaction_name}.dpot.new'))
                        _, dist_tgt_g, _ = readin_table(f"step_001/{interaction_name}.dist.tgt")
                        for i, dpot_file in enumerate(dpot_files):
                            step = int(re.search('step_(\d+)', dpot_file).group(1))
                            dpot_r, dpot_dU, _ = readin_table(dpot_file)
                            #dU_std.append((step, np.sqrt(np.trapz(x=dpot_r, y=(dist_tgt_g * dpot_dU)**2))))
                            #dU_std.append((step, np.trapz(x=dpot_r, y=np.abs(dist_tgt_g * dpot_dU))))
                            #dU_std.append((step, np.trapz(x=dpot_r, y=(dist_tgt_g * dpot_dU))))
                        # potential convergence inset
                        #axins0.plot(*zip(*dU_std))
                        #"""
                        # gather potential convergence 2 data
                    except:
                        pass
                    U_std = []
                    pot_files = sorted(glob.glob(f'step_*/{interaction_name}.pot.new'))
                    for i, pot_file in enumerate(pot_files):
                        step = int(re.search('step_(\d+)', pot_file).group(1))
                        pot_r, pot_U_step, _ = readin_table(pot_file)
                        #U_std.append((step, np.sqrt(np.trapz(x=pot_r, y=(dist_tgt_g * (pot_U_step - pot_U)**2)))))
                    # potential convergence 2 inset
                    #axins0.plot(*zip(*U_std[:-2]))
                    #"""
                    # plot rdf
                    try:
                        dist_r, dist_g, dist_flag = readin_table('step_020/A-A.dist.new')
                        ax1.plot(dist_r, dist_g, label=invset_short_names[inverse_setting['name']])
                    except:
                        print('.. no rdf data ..', system['name'], inverse_setting['name'])
                        ax1.plot([], [], label=invset_short_names[inverse_setting['name']])
                    # gather rdf convergence data
                    try:
                        dist_tgt_r, dist_tgt_g, _ = readin_table(f"step_001/{interaction_name}.dist.tgt")
                        g_std = []
                        dist_files = sorted(glob.glob(f'step_*/{interaction_name}.dist.new'))
                        for i, dist_file in enumerate(dist_files):
                            step = int(re.search('step_(\d+)', dist_file).group(1))
                            dist_r, dist_g, dist_flag = readin_table(dist_file)
                            if np.isclose(max(dist_r), system['r_max_u']):
                                noextend = slice(0, None)
                            else:
                                noextend = slice(0, np.argwhere(dist_r > system['r_max_u'])[0][0])
                            g_std.append((step, np.sqrt(1/max(dist_r) * np.trapz(x=dist_r[noextend], y=(dist_g[noextend] - dist_tgt_g[noextend])**2))))
                        # rdf convergence inset
                        line = axins1.plot(*zip(*g_std))
                    except:
                        print('.. no rdf convergence data ..', system['name'], inverse_setting['name'])
                        line = axins1.plot([], [])
                        raise
                    # legend lines
                    if s == 0:
                        label = invset_short_names[inverse_setting['name']]
                        legend_lines.append((line[0], label))

            # first column
            if s == 0:
                ax0.set_ylabel(r"$u_{20}(r)$ in kJ mol¯¹")
                ax1.set_ylabel(r"$g_{20}(r)$")
            ax0.set_xlim(system['r_max_u'] * np.array([0.29, 1.01]))
            ax0.set_ylim((-1.0, 3.3))
            ax1.set_ylim((0, 3.3))
            #ax1.set_ylim((0.90, 1.1))
            ax1.set_xlabel(r"$r$ in nm")

            axins1.set_xlim(0, 20)
            axins1.set_ylim(0.00, 0.006)
            axins1.set_xticks([0, 10, 20])
            #axins1.set_ylabel(r"$\delta$")
            # remove last tick
            ax1.yaxis.get_major_ticks()[-1].label1.set_visible(False)

            ax0.set_title(system_short_names.get(system['type'], system['type']))

        fig.legend(*zip(*legend_lines), loc=(0.20, 0.7), ncol=2, columnspacing=5.5)
        fig.tight_layout()    
        plt.subplots_adjust(hspace=0.0, wspace=0.0, right=0.99)
        fig.savefig(os.path.join(working_dir_base, "figures", f"method-comparison.pdf"))
        plt.show()

In [ ]:
run_bash("cp figures/method-comparison.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

## show jacobians

In [ ]:
vmin_vmax = {
    'lj/near-critical': (-5e-2, 5e-2),
    'lj/near-triple': (-8e-2, 8e-2),
    'spce': (-1.5e-2, 1.5e-2),
    'hexane': (-2e-2, 2e-2),
    'naphtalene': (-2e-2, 2e-2),
}

In [ ]:
from cycler import cycler
from matplotlib._layoutbox import plot_children
import matplotlib.ticker as ticker

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 150,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    #'axes.prop_cycle': (
        #cycler(color=['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B'])
        #+ cycler(ls=['-', '--', ':', (0, (5, 1)), '-.'])
    #),

}

cmap = plt.get_cmap('RdBu')

with mpl.rc_context(rc=mpl_rc):
    for s, system in enumerate(systems_to_show):
        print(s, system['name'])
        
        vmin, vmax = vmin_vmax[system['name']]
    
        n_inv = len(inverse_settings_to_show)
        fig = plt.figure(figsize=(7, 2), constrained_layout=True)
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.13, hspace=0.0, wspace=0.0)
        gs = mpl.gridspec.GridSpec(1, n_inv+1, width_ratios=[1]*n_inv+[0.1], wspace=0.0, figure=fig)
        axes = [None]*(n_inv+1)
        for a, ax in enumerate(axes):
            axes[a] = fig.add_subplot(gs[0, a])

        for i, inverse_setting in enumerate(inverse_settings_to_show):
            print(i, inverse_setting['name'])
            # once per system
            ax = axes[i]
            working_dir = system['name'] + '/' + inverse_setting['name']
            working_dir_parent = os.path.join(working_dir_base, system['name'])
            beta = 1 / oconst.k_gro / system['temperature']
            r_max_u = system['r_max_u']
            r_max_g = system['r_extend_g']

            with WorkingDir(working_dir):
                r, g_k, _ = readin_table('step_001/A-A.dist.new')
                r, g_tgt, _ = readin_table('step_001/A-A.dist.tgt')
                ndx_co = np.argwhere(r >= r_max_u)[0][0] + 1
                if inverse_setting['method']['method'] == 'ibi':
                    with np.errstate(invalid='ignore', divide='ignore'):
                        ibi_diag = np.nan_to_num(1 / (1/beta * np.log(g_tgt/g_k) / (g_k - g_tgt)))
                        ibi_jac = np.nan_to_num(np.diag(ibi_diag))
                    ax.imshow(ibi_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none', cmap=cmap)
                elif inverse_setting['method']['method'] == 'imc':
                    imc_mat = np.loadtxt("step_001/1.gmc")
                    n = len(system['moltypes'][0]['cg_repr'])
                    N = system['moltypes'][0]['nmols']
                    Delta_r = r[1] - r[0]
                    V = system['volume']
                    #print(n, N, Delta_r, V, beta)
                    with np.errstate(divide='ignore', invalid='ignore'):
                        imc_jac = beta * 1/((n*N)**2/V/2*4*np.pi*Delta_r) * np.diag(1/r**2) @ imc_mat
                    ax.imshow(imc_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none', cmap=cmap)
                elif inverse_setting['method']['method'] == 'iie':
                    if inverse_setting['method']['algorithm'] == 'newton':
                        data = np.load('step_001/newton-arrays.npz')
                        jac = data['jac']
                        # r=0 is cut in votca
                        jac = np.pad(jac, ((1, 0), (1, 0)), 'constant', constant_values=(0, 0))
                        im = ax.imshow(jac, vmin=vmin, vmax=vmax,
                                       extent=(0, r_max_g, r_max_g, 0), interpolation='none', cmap=cmap)
                        #ax.plot([0, r_max_u, r_max_u], [r_max_u, r_max_u, 0], linestyle=':', color='#d1495b')
                    elif inverse_setting['method']['algorithm'] == 'gauss-newton':
                        data = np.load('step_001/gauss-newton-arrays.npz')
                        jac_inv = data['jac_inv']
                        jac = np.linalg.inv(jac_inv)
                        # r=0 is cut in votca
                        jac = np.pad(jac, ((1, 0), (1, 0)), 'constant', constant_values=(0, 0))
                        im = ax.imshow(jac, vmin=vmin, vmax=vmax,
                                       #extent=(, r_max_u, r_max_u, 0),
                                       interpolation='none', cmap=cmap)
                        
            
            # remove last tick
            #ax.xaxis.get_major_ticks()[-1].label1.set_visible(False)

            ax.set_title(invset_short_names.get(inverse_setting['name'], inverse_setting['name']))

        for ax in axes[1:n_inv]:
            plt.setp(ax.get_yticklabels(), visible=False)
            #ax.set_xticks([0.4, 0.8])
        #for ax in axes:
            #ax.set_yticks([0.0, 0.4, 0.8])
            #ax.xaxis.set_major_locator(ticker.MultipleLocator(0.2))

        #axes[0].set_xticks([0.0, 0.4, 0.8])
        axes[0].set_ylabel('($g$ axis in nm)')
        axes[0].set_xlabel('($u$ axis in nm)')
        
        cb = fig.colorbar(im, cax=axes[-1], label=r"Jacobian in 1/(kJ/mol)")
        #cb.formatter.set_powerlimits((0, 0))
        #cb.ax.text(-0.03, 0.016, r'$\times$10$^{-2}$', va='bottom', ha='left', size=6)
        #cb.set_ticks(cb.ax.get_yticks())
        #cb.ax.set_yticklabels([-2, -1, 0, 1, 2])
        #cb.set_ticks([-0.015, 0, 0.015])
        #cb.ax.set_yticklabels([-1.5, 0, 1.5])
        #cb.ax.tick_params(direction='out')
        #plot_children(fig, fig._layoutbox, printit=False)
        plt.show()

### of first step water (paper)

In [ ]:
paper_jacobian_plots = {
    'spce': {
        'sys-inv-to-plot': [
            (systems_dict['spce'], invsets_dict['ibi-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['imc0.3-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['hncn-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['hncnedf-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['hncnex-hncinit-ibiintra']),
            #(systems_dict['spce'], invsets_dict['hncgned-hncinit-ibiintra']),
        ],
    },
}
vmin, vmax = -1.5e-2, 1.5e-2

invset_short_names = {
    'ibi-hncinit-ibiintra': 'IBI',
    'imc0.3-hncinit-ibiintra': 'IMC',
    'hncn-hncinit-ibiintra': 'HNCN (sd)',
    'hncned-hncinit-ibiintra': 'HNCN (jc)',
    'hncnedf-hncinit-ibiintra': 'HNCN',
    'hncnex-hncinit-ibiintra': 'HNCN (ex)',
    'hncgned-hncinit-ibiintra': 'HNCGN',
}

system_short_names = {}

In [ ]:
from cycler import cycler
from matplotlib._layoutbox import plot_children
import matplotlib.ticker as ticker

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 150,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    #'axes.prop_cycle': (
        #cycler(color=['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B'])
        #+ cycler(ls=['-', '--', ':', (0, (5, 1)), '-.'])
    #),

}

with mpl.rc_context(rc=mpl_rc):
    for paper_jacobian_plot_name, paper_jacobian_plot in paper_jacobian_plots.items():
    
        n_sys_inv = len(paper_jacobian_plot['sys-inv-to-plot'])
        fig = plt.figure(figsize=(4.77, 1.35), constrained_layout=True)
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.13, hspace=0.0, wspace=0.0)
        gs = mpl.gridspec.GridSpec(1, n_sys_inv+1, width_ratios=[1]*n_sys_inv+[0.1], wspace=0.0, figure=fig)
        axes = [None]*(n_sys_inv+1)
        axes[0] = fig.add_subplot(gs[0, 0])
        axes[1] = fig.add_subplot(gs[0, 1])
        axes[2] = fig.add_subplot(gs[0, 2])
        axes[3] = fig.add_subplot(gs[0, 3])
        axes[4] = fig.add_subplot(gs[0, 4])
        axes[5] = fig.add_subplot(gs[0, 5])

        for s, (system, inverse_setting) in enumerate(paper_jacobian_plot['sys-inv-to-plot']):
            print(s, system['name'], inverse_setting['name'])
            # once per system
            ax = axes[s]
            working_dir = system['name'] + '/' + inverse_setting['name']
            working_dir_parent = os.path.join(working_dir_base, system['name'])
            beta = 1 / oconst.k_gro / system['temperature']
            r_max_u = system['r_max_u']

            with WorkingDir(working_dir):
                r, g_k, _ = readin_table('step_001/A-A.dist.new')
                r, g_tgt, _ = readin_table('step_001/A-A.dist.tgt')
                ndx_co = np.argwhere(r >= r_max_u)[0][0] + 1
                print(ndx_co, f"{max(r):.30f}")
                if inverse_setting['method']['method'] == 'ibi':
                    with np.errstate(invalid='ignore', divide='ignore'):
                        ibi_diag = np.nan_to_num(1 / (1/beta * np.log(g_tgt/g_k) / (g_k - g_tgt)))
                        ibi_jac = np.nan_to_num(np.diag(ibi_diag))
                        print(ibi_jac.shape)
                    ax.imshow(ibi_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none')
                elif inverse_setting['method']['method'] == 'imc':
                    imc_mat = np.loadtxt("step_001/1.gmc")
                    n = len(system['moltypes'][0]['cg_repr'])
                    N = system['moltypes'][0]['nmols']
                    Delta_r = r[1] - r[0]
                    V = system['volume']
                    print(n, N, Delta_r, V, beta)
                    with np.errstate(divide='ignore', invalid='ignore'):
                        imc_jac = beta * 1/((n*N)**2/V/2*4*np.pi*Delta_r) * np.diag(1/r**2) @ imc_mat
                    print(imc_jac.shape)
                    ax.imshow(imc_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none')
                elif inverse_setting['method']['method'] == 'iie':
                    if inverse_setting['method']['algorithm'] == 'newton':
                        data = np.load('step_001/newton-arrays.npz')
                        jac = data['jac']
                        # r=0 is cut in votca
                        jac = np.pad(jac, ((1, 0), (1, 0)), 'constant', constant_values=(0, 0))
                        print(jac.shape)
                        if inverse_setting['extend-g']:
                            im = ax.imshow(jac[:ndx_co, :ndx_co], vmin=vmin, vmax=vmax,
                                           extent=(0, r_max_u, r_max_u, 0), interpolation='none')
                        else:
                            im = ax.imshow(jac, vmin=vmin, vmax=vmax,
                                           extent=(0, r_max_u, r_max_u, 0), interpolation='none')
                            #ax.plot([0, r_max_u, r_max_u], [r_max_u, r_max_u, 0], linestyle=':', color='#d1495b')
                        
            
            # remove last tick
            #ax.xaxis.get_major_ticks()[-1].label1.set_visible(False)

            ax.set_title(invset_short_names.get(inverse_setting['name'], inverse_setting['name']))

        for ax in axes[1:5]:
            plt.setp(ax.get_yticklabels(), visible=False)
            ax.set_xticks([0.4, 0.8])
        for ax in axes:
            ax.set_yticks([0.0, 0.4, 0.8])
            #ax.xaxis.set_major_locator(ticker.MultipleLocator(0.2))

        axes[0].set_xticks([0.0, 0.4, 0.8])
        axes[0].set_ylabel('($g$ axis in nm)')
        axes[0].set_xlabel('($u$ axis in nm)')
        
        cb = fig.colorbar(im, cax=axes[-1], label=r"Jacobian in 1/(kJ/mol)")
        #cb.formatter.set_powerlimits((0, 0))
        cb.ax.text(-0.03, 0.016, r'$\times$10$^{-2}$', va='bottom', ha='left', size=6)
        #cb.set_ticks(cb.ax.get_yticks())
        #cb.ax.set_yticklabels([-2, -1, 0, 1, 2])
        cb.set_ticks([-0.015, 0, 0.015])
        cb.ax.set_yticklabels([-1.5, 0, 1.5])
        cb.ax.tick_params(direction='out')
        #plot_children(fig, fig._layoutbox, printit=False)
        fig.savefig(os.path.join(working_dir_base, "figures", f"jacobian-comparison-spce.pdf"), dpi=300)
        plt.show()

In [ ]:
run_bash("cp figures/jacobian-comparison-spce.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

### toc plot

In [ ]:
paper_jacobian2_plots = {
    'spce': {
        'sys-inv-to-plot': [
            (systems_dict['spce'], invsets_dict['ibi-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['imc0.3-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['hncn-hncinit-ibiintra']),
            (systems_dict['spce'], invsets_dict['hncnedf-hncinit-ibiintra']),
            #(systems_dict['spce'], invsets_dict['hncnex-hncinit-ibiintra']),
            #(systems_dict['spce'], invsets_dict['hncgned-hncinit-ibiintra']),
        ],
    },
}


system_short_names = {}

In [ ]:
from cycler import cycler
from matplotlib._layoutbox import plot_children
import matplotlib.ticker as ticker

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 150,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'mathtext.fontset': 'stix',
    #'font.family': 'STIXGeneral',
    'xtick.top': False,
    'ytick.right': False,
    'xtick.bottom': False,
    'ytick.left': False,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    #'axes.prop_cycle': (
        #cycler(color=['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B'])
        #+ cycler(ls=['-', '--', ':', (0, (5, 1)), '-.'])
    #),

}

vmin, vmax = -1.5e-2, 1.5e-2

with mpl.rc_context(rc=mpl_rc):
    for paper_jacobian_plot_name, paper_jacobian_plot in paper_jacobian2_plots.items():
    
        n_sys_inv = len(paper_jacobian_plot['sys-inv-to-plot'])
        fig, axes = plt.subplots(ncols=n_sys_inv, figsize=(3.8, 1.2),  constrained_layout=True)
        fig.set_constrained_layout_pads(wspace=0.0, w_pad=0.03)

        for s, (system, inverse_setting) in enumerate(paper_jacobian_plot['sys-inv-to-plot']):
            print(s, system['name'], inverse_setting['name'])
            # once per system
            ax = axes[s]
            working_dir = system['name'] + '/' + inverse_setting['name']
            working_dir_parent = os.path.join(working_dir_base, system['name'])
            beta = 1 / oconst.k_gro / system['temperature']
            r_max_u = system['r_max_u']

            with WorkingDir(working_dir):
                r, g_k, _ = readin_table('step_001/A-A.dist.new')
                r, g_tgt, _ = readin_table('step_001/A-A.dist.tgt')
                ndx_co = np.argwhere(r >= r_max_u)[0][0] + 1
                print(ndx_co, f"{max(r):.30f}")
                if inverse_setting['method']['method'] == 'ibi':
                    with np.errstate(invalid='ignore', divide='ignore'):
                        ibi_diag = np.nan_to_num(1 / (1/beta * np.log(g_tgt/g_k) / (g_k - g_tgt)))
                        ibi_jac = np.nan_to_num(np.diag(ibi_diag))
                        print(ibi_jac.shape)
                    ax.imshow(ibi_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none')
                elif inverse_setting['method']['method'] == 'imc':
                    imc_mat = np.loadtxt("step_001/1.gmc")
                    n = len(system['moltypes'][0]['cg_repr'])
                    N = system['moltypes'][0]['nmols']
                    Delta_r = r[1] - r[0]
                    V = system['volume']
                    print(n, N, Delta_r, V, beta)
                    with np.errstate(divide='ignore', invalid='ignore'):
                        imc_jac = beta * 1/((n*N)**2/V/2*4*np.pi*Delta_r) * np.diag(1/r**2) @ imc_mat
                    ax.imshow(imc_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none')
                elif inverse_setting['method']['method'] == 'iie':
                    if inverse_setting['method']['algorithm'] == 'newton':
                        data = np.load('step_001/newton-arrays.npz')
                        if inverse_setting['extend-g']:
                            im = ax.imshow(data['jac'][:ndx_co, :ndx_co], vmin=vmin, vmax=vmax, 
                                           extent=(0, r_max_u, r_max_u, 0), interpolation='none')
                        else:
                            im = ax.imshow(data['jac'][:ndx_co, :ndx_co], vmin=vmin, vmax=vmax, 
                                           extent=(0, r_max_u, r_max_u, 0), interpolation='none')
                            
            ax.set_title(invset_short_names.get(inverse_setting['name'], inverse_setting['name']), pad=2.5)

        for ax in axes:
            #plt.setp(ax.get_xticklabels(), visible=False)
            #plt.setp(ax.get_yticklabels(), visible=False)
            ax.xaxis.set_major_locator(plt.NullLocator())
            ax.yaxis.set_major_locator(plt.NullLocator())

        axes[0].set_ylabel('($g$ axis)')
        axes[0].set_xlabel('($u$ axis)')
        axes[0].text(0.07, 0.64, r"$\frac{dg}{du}$", size=24, color='white')
        fig.savefig(os.path.join(working_dir_base, "figures", f"toc-picture.pdf"), dpi=300)
        plt.show()

In [ ]:
run_bash("cp figures/toc-picture.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

### compare jacobians imc, hncn (hexane, naphtalene) (paper)

In [ ]:
paper_jacobian_plots = {
    'hex/naph': {
        'sys-inv-to-plot': [
            (systems_dict['hexane'], invsets_dict['imc0.3-hncinit-ibiintra']),
            (systems_dict['hexane'], invsets_dict['hncned-hncinit-ibiintra']),
            (systems_dict['naphtalene'], invsets_dict['imc0.3-hncinit-ibiintra']),
            (systems_dict['naphtalene'], invsets_dict['hncned-hncinit-ibiintra']),
        ],
    },
}

invset_short_names = {
    'imc0.3-hncinit-ibiintra': 'IMC',
    'hncned-hncinit-ibiintra': 'HNCN',
}

system_short_names = {}

In [ ]:
from cycler import cycler
from matplotlib._layoutbox import plot_children

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 150,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    #'axes.prop_cycle': (
        #cycler(color=['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B'])
        #+ cycler(ls=['-', '--', ':', (0, (5, 1)), '-.'])
    #),

}

vmin, vmax = -2e-2, 2e-2

with mpl.rc_context(rc=mpl_rc):
    for paper_jacobian_plot_name, paper_jacobian_plot in paper_jacobian_plots.items():
    
        n_sys_inv = len(paper_jacobian_plot['sys-inv-to-plot'])
        fig = plt.figure(figsize=(4.77, 1.4), constrained_layout=True)
        fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.035, hspace=0.0, wspace=0.0)
        gs = mpl.gridspec.GridSpec(1, n_sys_inv+1, width_ratios=[1]*n_sys_inv+[0.1], wspace=0.0, figure=fig)
        axes = [None]*5
        axes[0] = fig.add_subplot(gs[0, 0])
        axes[1] = fig.add_subplot(gs[0, 1])
        axes[2] = fig.add_subplot(gs[0, 2])
        axes[3] = fig.add_subplot(gs[0, 3])
        axes[4] = fig.add_subplot(gs[0, 4])

        for s, (system, inverse_setting) in enumerate(paper_jacobian_plot['sys-inv-to-plot']):
            print(s, system['name'], inverse_setting['name'])
            # once per system
            ax = axes[s]
            working_dir = system['name'] + '/' + inverse_setting['name']
            working_dir_parent = os.path.join(working_dir_base, system['name'])
            beta = 1 / oconst.k_gro / system['temperature']
            r_max_u = system['r_max_u']

            with WorkingDir(working_dir):
                r, g_k, _ = readin_table('step_001/A-A.dist.new')
                r, g_tgt, _ = readin_table('step_001/A-A.dist.tgt')
                ndx_co = np.argwhere(r >= r_max_u)[0][0]
                print(ndx_co)
                if inverse_setting['method']['method'] == 'ibi':
                    with np.errstate(invalid='ignore', divide='ignore'):
                        ibi_diag = np.nan_to_num(1 / (1/beta * np.log(g_tgt/g_k) / (g_k - g_tgt)))
                        ibi_jac = np.nan_to_num(np.diag(ibi_diag))
                    ax.imshow(ibi_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none')
                elif inverse_setting['method']['method'] == 'imc':
                    imc_mat = np.loadtxt("step_001/1.gmc")
                    n = len(system['moltypes'][0]['cg_repr'])
                    N = system['moltypes'][0]['nmols']
                    Delta_r = r[1] - r[0]
                    V = system['volume']
                    print(n, N, Delta_r, V, beta)
                    with np.errstate(divide='ignore', invalid='ignore'):
                        imc_jac = beta * 1/((n*N)**2/V/2*4*np.pi*Delta_r) * np.diag(1/r**2) @ imc_mat
                    ax.imshow(imc_jac, vmin=vmin, vmax=vmax, extent=(0, max(r), max(r), 0), interpolation='none')
                elif inverse_setting['method']['method'] == 'iie':
                    if inverse_setting['method']['algorithm'] == 'newton':
                        data = np.load('step_001/newton-arrays.npz')
                        if inverse_setting['extend-g']:
                            im = ax.imshow(data['jac'][:ndx_co, :ndx_co], vmin=vmin, vmax=vmax,
                                           extent=(0, r_max_u, r_max_u, 0), interpolation='none')
                        else:
                            im = ax.imshow(data['jac'], vmin=vmin, vmax=vmax,
                                           extent=(0, r_max_u, r_max_u, 0), interpolation='none')
                            #ax.plot([0, r_max_u, r_max_u], [r_max_u, r_max_u, 0], linestyle=':', color='#d1495b')
                        
            
            # remove last tick
            #ax.xaxis.get_major_ticks()[-1].label1.set_visible(False)

            ax.set_title(invset_short_names.get(inverse_setting['name'], inverse_setting['name']))

        for ax in axes[1:4]:
            plt.setp(ax.get_yticklabels(), visible=False)
            ax.set_xticks([0.4, 0.8, 1.2])
        for ax in axes:
            ax.set_yticks([0.0, 0.4, 0.8, 1.2])
        axes[0].set_xticks([0.0, 0.4, 0.8, 1.2])
        axes[0].set_ylabel('($g$ axis in nm)')
        axes[0].set_xlabel('($u$ axis in nm)')
        
        cb = fig.colorbar(im, cax=axes[-1], label=r"Jacobian in 1/(kJ/mol)")
        #cb.formatter.set_powerlimits((0, 0))
        cb.ax.text(-0.03, 0.021, r'$\times$10$^{-2}$', va='bottom', ha='left', size=6)
        cb.set_ticks(cb.ax.get_yticks())
        cb.ax.set_yticklabels([-2, -1, 0, 1, 2])
        cb.ax.tick_params(direction='out')
        #plot_children(fig, fig._layoutbox, printit=False)
        fig.savefig(os.path.join(working_dir_base, "figures", f"jacobian-comparison-hex-naph.pdf"), dpi=300)
        plt.show()

In [ ]:
run_bash("cp figures/jacobian-comparison-hex-naph.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

## compare cut outs of jacobian

In [ ]:
from cycler import cycler
from matplotlib._layoutbox import plot_children
import matplotlib.patches as patches

SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 150,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
    #'axes.prop_cycle': (
        #cycler(color=['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B'])
        #+ cycler(ls=['-', '--', ':', (0, (5, 1)), '-.'])
    #),

}
colors = ['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B']

vmin, vmax = -1e-2, 1e-2

system, inverse_setting = systems_dict['naphtalene'], invsets_dict['hncned-hncinit-ibiintra']

with mpl.rc_context(rc=mpl_rc):
    fig, ax = plt.subplots(figsize=(4.77/2, 1.4), constrained_layout=True)
    fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.0, hspace=0.0, wspace=0.0)

    working_dir = system['name'] + '/' + inverse_setting['name']
    working_dir_parent = os.path.join(working_dir_base, system['name'])
    beta = 1 / oconst.k_gro / system['temperature']
    r_max_u = system['r_max_u']

    with WorkingDir(working_dir):
        r, g_k, _ = readin_table('step_001/A-A.dist.new')
        r, g_tgt, _ = readin_table('step_001/A-A.dist.tgt')
        Delta_r = r[1] - r[0]
        ndx_co = np.argwhere(r >= r_max_u)[0][0]
        max_r = max(r)
        data = np.load('step_001/newton-arrays.npz')
        im = ax.imshow(data['jac'], vmin=vmin, vmax=vmax, extent=(0, max_r, max_r, 0), interpolation='none')
        rect = patches.Rectangle((Delta_r, Delta_r), r_max_u, max_r-3*Delta_r, linewidth=1.5, edgecolor=colors[1], facecolor='none', linestyle='--')
        ax.add_patch(rect)
        #rect = patches.Rectangle((Delta_r, Delta_r), max_r-3*Delta_r, r_max_u, linewidth=1.5, edgecolor=colors[-1], facecolor='none', linestyle='-.')
        #ax.add_patch(rect)
        rect = patches.Rectangle((Delta_r, Delta_r), r_max_u, r_max_u, linewidth=1.5, edgecolor=colors[0], facecolor='none', linestyle=':')
        ax.add_patch(rect)

    ax.set_xticks([0.0, 0.8, 1.6, 2.4])
    ax.set_yticks([0.0, 0.8, 1.6, 2.4])
    ax.set_ylabel('($g$ axis in nm)')
    ax.set_xlabel('($u$ axis in nm)')

    cb = fig.colorbar(im, ax=ax, label=r"Jacobian in 1/(kJ/mol)", pad=-0.04)
    #cb.formatter.set_powerlimits((0, 0))
    cb.ax.text(-0.02, 0.0100, r'$\times$10$^{-2}$', va='bottom', ha='left', size=6)
    cb.set_ticks(cb.ax.get_yticks())
    cb.ax.set_yticklabels([-1.0, -0.5, 0.0, 0.5, 1.0])
    cb.ax.tick_params(direction='out')
    #plot_children(fig, fig._layoutbox, printit=False)
    fig.savefig(os.path.join(working_dir_base, "figures", f"jacobian-comparison-cut-outs.pdf"), dpi=300)
    plt.show()

In [ ]:
run_bash("cp figures/jacobian-comparison-cut-outs.pdf /home/marvin/research/output/iie-singlebead-paper/figures/");

## show RDF extrapolation for paper

In [ ]:
import importlib
iie_script = "/home/marvin/research/code/votca/csg/share/scripts/inverse/iie.py"
spec = importlib.util.spec_from_file_location("iie", iie_script)
iie = importlib.util.module_from_spec(spec)
spec.loader.exec_module(iie)

In [ ]:
SMALL_SIZE = 8
MEDIUM_SIZE = 10
BIGGER_SIZE = 12
mpl_rc = {
    'figure.dpi': 150,
    'legend.frameon': False,
    'legend.labelspacing': 0.1,
    'legend.columnspacing': 0.4,
    'legend.handlelength': 2.0,
    'font.size': SMALL_SIZE,          # controls default text sizes
    'axes.titlesize': SMALL_SIZE,     # fontsize of the axes title
    'axes.labelsize': SMALL_SIZE,    # fontsize of the x and y labels
    'xtick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'ytick.labelsize': SMALL_SIZE,    # fontsize of the tick labels
    'legend.fontsize': SMALL_SIZE,    # legend fontsize
    'figure.titlesize': MEDIUM_SIZE,  # fontsize of the figure title
    'xtick.top': True,
    'ytick.right': True,
    'xtick.direction': 'in',
    'ytick.direction': 'in',
}
colors = ['#EDAE49', '#D1495B', '#4E88B7', '#00798C', '#003D5B']

system, inverse_setting = systems_dict['spce'], invsets_dict['hncn-hncinit-ibiintra']

with mpl.rc_context(rc=mpl_rc):
    fig, ax = plt.subplots(figsize=(4.77/2, 1.4), constrained_layout=True)
    fig.set_constrained_layout_pads(w_pad=0.0, h_pad=0.0, hspace=0.0, wspace=0.0)

    working_dir = system['name'] + '/' + inverse_setting['name']
    working_dir_parent = os.path.join(working_dir_base, system['name'])
    beta = 1 / oconst.k_gro / system['temperature']
    r_max_u = system['r_max_u']

    with WorkingDir(working_dir):
        r, g_tgt, _ = readin_table('step_001/A-A.dist.tgt')
        
    delta_r = r[1] - r[0]
    r_long = np.arange(r[0], r[-1] * 2.0, delta_r)
    g_tgt_extrap0 = iie.extrapolate_g(r, r_long, g_tgt, np.zeros_like(r), 1, system['density'], k_max=0)
    g_tgt_extrap = iie.extrapolate_g(r, r_long, g_tgt, np.zeros_like(r), 1, system['density'], k_max=5)
    
    fig, ax = plt.subplots(ncols=1, figsize=(4.77/2, 1.8))
    ax.plot(r, rdf_target_g - 1, label=r'$h$', color=colors[0])
    ax.plot(r_long, g_tgt_extrap0 - 1, label=r'$h^\dagger_\mathrm{ext0}$', color=colors[1], linestyle='-.')
    ax.plot(r_long, g_tgt_extrap - 1, label='$h^\dagger_{\mathrm{ext,}5}$', color=colors[2], linestyle='--')

    ax.legend()
    ax.axvline(r[ndx_co], linestyle=':', color='#aaaaaa')
    ax.set_xlim(0, max(r_long))
    ax.set_ylim(-0.1, 0.1)
    fig.savefig('figures/rdf-extrapolation.pdf', dpi=300)
    plt.show()

# run CG system in NPT

### prepare

In [ ]:
systems_to_npt = systems[2:3]
steps_to_npt = ['p-hncgn-6/hncinit/step_020']

In [ ]:
for system in systems_to_npt:
    print(f"system {system['name']}")
    for step in steps_to_npt:
          
        working_dir, step_dir = os.path.split(os.path.join(working_dir_base, system['name'], step))
        npt_dir = "npt-" + step_dir
          
        with WorkingDir(working_dir):
            run_bash(f"mkdir -p {npt_dir}")
            run_bash(f"cp {template_dir}/{system['type']}/cg/grompp-npt.mdp {npt_dir}/grompp.mdp")
            run_bash(f"cp topol.top {npt_dir}/topol.top")
            run_bash(f"cp index.ndx {npt_dir}/index.ndx")
            run_bash(f"cp {step_dir}/table_A_A.xvg {npt_dir}/table_A_A.xvg")
            run_bash(f"cp {step_dir}/confout.gro {npt_dir}/conf.gro")
            run_bash(f"cp table.xvg {npt_dir}/table.xvg")
            # run length
            gt.mdp.set_parameter(f"{npt_dir}/grompp.mdp", 'nsteps', 10000)
            # set temperature
            gt.mdp.set_parameter(f"{npt_dir}/grompp.mdp", 'ref-t', system['temperature'])
            # set pressure
            run_bash(f"gmx energy -f ../../prod/ener.edr -o energy-temp.xvg <<< 'pressure'")
            pressure, _ = gt.xvg.load("energy-temp.xvg")
            run_bash("rm -f energy-temp.xvg")
            pressure_target = pressure['Pressure'].mean()
            gt.mdp.set_parameter(f"{npt_dir}/grompp.mdp", 'ref-p', pressure_target)
            # set cut off
            for tag in ('rlist', 'rcoulomb', 'rvdw'):
                gt.mdp.set_parameter(f"{npt_dir}/grompp.mdp", tag, system['r_max_u'])

### run manually

In [ ]:
# grompp
# mdrun
# energy

### show volume

In [ ]:
for system in systems_to_npt:
    print(f"system {system['name']}")
    for step in steps_to_npt:
          
        working_dir, step_dir = os.path.split(os.path.join(working_dir_base, system['name'], step))
        npt_dir = "npt-" + step_dir
          
        with WorkingDir(working_dir):
            data_aa, header = gt.xvg.load(f"../../npt/energy.xvg")
            data_cg, header = gt.xvg.load(f"{npt_dir}/energy.xvg")
          
            plt.figure(figsize=(5, 3))
            plt.plot(data_aa['Time (ps)'], data_aa['Volume'], ':', label='AA')
            plt.plot(data_cg['Time (ps)'], data_cg['Volume'], label='CG')
            plt.xlim(0, 50)
            plt.legend()   
            plt.xlabel('t in ps')
            plt.ylabel('V in nm³')
            plt.title('5000 water molecules, NPT\nParrinello-Rahman barostat (247 bar, 5 ps)')
            plt.tight_layout()
            plt.savefig(os.path.join(working_dir_base, "figures", f"npt-comparison-{method.replace('/', '-')}_{system['name'].replace('/', '-')}.png"), dpi=150)
            plt.show()

## plots for presentations

In [ ]:
# p-change
methods_to_show = ['p-hncgn-2/biinit-p-change']
systems_to_show = systems[0:1]

for system in systems_to_show:
    print("system", system['name'])
    # find target pressure
    run_bash(f"gmx energy -f {system['name']}/prod/ener.edr -o energy-temp.xvg <<< 'pressure'")
    pressure, _ = gt.xvg.load("energy-temp.xvg")
    pressure_target = pressure['Pressure'].mean()
    run_bash("rm -f energy-temp.xvg")
    for method in methods_to_show:
        print("method", method)
        working_dir = os.path.join(working_dir_base, system['name'], method)
        
        fig, ax2 = plt.subplots(nrows=1, ncols=1, figsize=[6, 4])

        with WorkingDir(working_dir):
            ener_files = sorted(glob.glob('step_*/ener.edr'))
            if ener_files == []:
                continue
            steps = []
            pressures = []
            pressures_std = []
            for ener_file in ener_files:
                if os.stat(ener_file).st_size == 0:
                    continue
                step = int(re.search('step_(\d+)', ener_file).group(1))
                run_bash(f"gmx energy -f {ener_file} -o /tmp/energy-temp.xvg <<< 'Temperature\nPressure'")
                data, header = gt.xvg.load("/tmp/energy-temp.xvg")
                steps.append(step)
                pressures.append(data[data['Time (ps)'] > 10]['Pressure'].mean())
                pressures_std.append(data[data['Time (ps)'] > 10]['Pressure'].std())
                run_bash(f"rm -f /tmp/energy-temp.xvg")
            ax2.errorbar(steps, pressures, pressures_std, label='MD pressure')
            # plot target pressure
            ax2.plot([1, 10, 11, 20], [pressure_target, pressure_target, pressure_target*2, pressure_target*2], linestyle=':', label='target pressure')
            ax2.set_ylim((-2*pressure_target, 8*pressure_target))
            # calculate virial pressures
            pressures_vir = []
            for step in steps:
                pot_file = f"step_{step:03d}/A-A.pot.cur"
                rdf_file = f"step_{step:03d}/A-A.dist.new"
                if (not os.path.exists(pot_file)) or (not os.path.exists(rdf_file)):
                    pressures_vir.append(None)
                    continue
                r, U, _ = readin_table(pot_file)
                r, g, _ = readin_table(rdf_file)
                density = system['top'].nmols() / system['volume']
                kBT = oconst.k_gro * system['temperature']
                pressure_vir = calc_pressure_bar1(r, g, U, density, kBT, system['r_max_u'], 1e-10)
                pressures_vir.append(pressure_vir)
             
            ax2.plot(steps, pressures_vir, label='virial pressure')
                 

        #ax2.set_title("Pressure vs. step")
        ax2.legend()
        ax2.legend()
        ax2.set_xlabel('step')
        ax2.set_ylabel('pressure in bar')
        fig.tight_layout()    
        fig.savefig(os.path.join(working_dir_base, "figures", f"{method.replace('/', '-')}_{system['name'].replace('/', '-')}.png"), dpi=150)
        plt.show()

In [ ]:
# p-hncng
methods_to_show = ['ihnc/hncinit', 'p-hncgn-2/biinit']
systems_to_show = systems

for system in systems_to_show:
    print("system", system['name'])
    # find target pressure
    run_bash(f"gmx energy -f {system['name']}/prod/ener.edr -o energy-temp.xvg <<< 'pressure'")
    pressure, _ = gt.xvg.load("energy-temp.xvg")
    pressure_target = pressure['Pressure'].mean()
    run_bash("rm -f energy-temp.xvg")
    for method in methods_to_show:
        print("method", method)
        working_dir = os.path.join(working_dir_base, system['name'], method)
        
        fig, ax2 = plt.subplots(nrows=1, ncols=1, figsize=[5, 3])

        with WorkingDir(working_dir):
            ener_files = sorted(glob.glob('step_*/ener.edr'))
            if ener_files == []:
                continue
            steps = []
            pressures = []
            pressures_std = []
            for ener_file in ener_files:
                if os.stat(ener_file).st_size == 0:
                    continue
                step = int(re.search('step_(\d+)', ener_file).group(1))
                run_bash(f"gmx energy -f {ener_file} -o /tmp/energy-temp.xvg <<< 'Temperature\nPressure'")
                data, header = gt.xvg.load("/tmp/energy-temp.xvg")
                steps.append(step)
                pressures.append(data[data['Time (ps)'] > 10]['Pressure'].mean())
                pressures_std.append(data[data['Time (ps)'] > 10]['Pressure'].std())
                run_bash(f"rm -f /tmp/energy-temp.xvg")
            ax2.errorbar(steps, pressures, pressures_std, label='MD pressure')
            # plot target pressure
            ax2.axhline(pressure_target, linestyle=':', label='target pressure')
            #ax2.set_ylim((-1*pressure_target, 3*pressure_target))
            # calculate virial pressures
            pressures_vir = []
            for step in steps:
                pot_file = f"step_{step:03d}/A-A.pot.cur"
                rdf_file = f"step_{step:03d}/A-A.dist.new"
                if (not os.path.exists(pot_file)) or (not os.path.exists(rdf_file)):
                    pressures_vir.append(None)
                    continue
                r, U, _ = readin_table(pot_file)
                r, g, _ = readin_table(rdf_file)
                density = system['top'].nmols() / system['volume']
                kBT = oconst.k_gro * system['temperature']
                pressure_vir = calc_pressure_bar1(r, g, U, density, kBT, system['r_max_u'], 1e-10)
                pressures_vir.append(pressure_vir)
             
            ax2.plot(steps, pressures_vir, label='virial pressure')
                 
        ax2.legend()
        ax2.set_xlabel('step')
        ax2.set_ylabel('pressure in bar')
        fig.tight_layout()    
        fig.savefig(os.path.join(working_dir_base, "figures", f"p-convergence_{method.replace('/', '-')}_{system['name'].replace('/', '-')}.png"), dpi=150)
        plt.show()

In [ ]:
cmap = plt.get_cmap('rainbow')

#methods_to_show = ['ibi/biinit', 'ibi/hncinit', 'ihnc/biinit', 'ihnc/hncinit', 'ihnc/ibiinit', 'hncgn/biinit']
#methods_to_show = ['ibi/ihncinit', 'ihnc/ibiinit']
#methods_to_show = ['ihnc/biinit']
#methods_to_show = ['ihnc/biinit', 'hncgn/biinit']
#methods_to_show = ['ibi/biinit']
#methods_to_show = ['p-hncgn-1/tableinit', 'p-hncgn-1/tableinit2']
#methods_to_show = ['hncgn/biinit', 'p-hncgn-1/biinit', 'p-hncgn-1/tableinit']
#systems_to_show = systems[0:1] + systems[3:4]
#methods_to_show = ['p-hncgn-1/biinit', 'p-hncgn-1/hncinit']
methods_to_show = ['p-hncgn-2/biinit', 'p-hncgn-2/hncinit']
#methods_to_show = ['p-hncgn-3/biinit', 'p-hncgn-3/hncinit']
#methods_to_show = ['p-hncgn-4/biinit', 'p-hncgn-4/hncinit']
#methods_to_show = ['p-hncgn-5/biinit', 'p-hncgn-5/hncinit']
#methods_to_show = ['p-hncgn-1/biinit', 'p-hncgn-1/hncinit', 'p-hncgn-2/biinit', 'p-hncgn-2/hncinit']
#methods_to_show = ['p-hncgn-2/hncinit']
#methods_to_show = ['p-hncgn-2/biinit-p-change']
#methods_to_show = ['p-hncgn-4/biinit-double-p']
#systems_to_show = systems[0:1]
systems_to_show = systems[0:3]
#comparisons_to_show = ['ihnc/hncinit/step_010', 'ibi/biinit/step_200']
#comparisons_to_show = ['ihnc/biinit/step_010']
#comparisons_to_show = ['hncgn/biinit/step_010']
comparisons_to_show = []

for system in systems_to_show:
    print("system", system['name'])
    for method in methods_to_show:
        print("method", method)
        working_dir_parent = os.path.join(working_dir_base, system['name'])
        working_dir = os.path.join(working_dir_base, system['name'], method)
    
        
        with WorkingDir(working_dir):
            if len(glob.glob('step_*/')) <= 1:
                continue
                
            fig, (ax0, ax1, ax2) = plt.subplots(nrows=1, ncols=3, figsize=[16, 5])
                
            # plot g(r)
            dist_files = sorted(glob.glob('step_*/A-A.dist.new'))
            max_step = int(re.search('step_(\d+)', dist_files[-1]).group(1))
            dist_files = dist_files[::max(max_step//8, 1)]
            for dist_file in dist_files:
                step = int(re.search('step_(\d+)', dist_file).group(1))
                dist_r, dist_g, dist_flag = readin_table(dist_file)
                #print(dist_g[40:50])
                ax0.plot(dist_r, dist_g, label=f"step {step}", color=cmap(step/max_step))
                ax0.set_title("g(r)")

            # plot dU(r)  
            dpot_files = sorted(glob.glob('step_*/A-A.dpot.new'))
            dpot_files = dpot_files[::max(max_step//8, 1)]
            for dpot_file in dpot_files:
                step = int(re.search('step_(\d+)', dpot_file).group(1))
                dpot_r, dpot_dU, dist_flag = readin_table(dpot_file)
                ax1.plot(dpot_r, dpot_dU, '.-', label=f"step {step}", color=cmap(step/max_step))
                #ax1.plot([0.88, 0.88], [-100, 100], '--')
                #print(dpot_r[40:50])
                #print(dpot_dU[40:50])
                ax1.set_title("ΔU(r)")
                ax1.set_ylim((-1, 1))
                #ax1.set_ylim((-100, 100))

            # plot U(r)
            pot_files = sorted(glob.glob('step_*/A-A.pot.new'))
            pot_files = pot_files[::max(max_step//8, 1)]
            for pot_file in pot_files:
                step = int(re.search('step_(\d+)', pot_file).group(1))
                pot_r, pot_U, dist_flag = readin_table(pot_file)
                ax2.plot(pot_r, pot_U, label=f"step {step}", color=cmap(step/max_step))
                ax2.set_ylim((-2, 3))
                #ax2.set_ylim((-20, 100))
                ax2.set_title("U(r)")

            # plot target g(r) and U(r)
            dist_r, dist_g, dist_flag = readin_table("A-A.dist.tgt")
            ax0.plot(dist_r, dist_g, label="target", color='k', linestyle='--')
            if system['type'] == 'lj':
                tgt_r = dist_r[1:]
                pot_target = 4 * ((1/tgt_r)**12 - (1/tgt_r)**6)
                ax2.plot(tgt_r, pot_target, label="target", color='k', linestyle='--')
                
            # plot comparisons
            for comparison in comparisons_to_show:
                with WorkingDir(working_dir_parent):
                    pot_r, pot_U, pot_flag = readin_table(f"{comparison}/A-A.pot.new")
                ax2.plot(pot_r, pot_U, label=comparison, linestyle='--')

            ax0.legend() #loc='center left')
            ax1.legend() #loc='upper right')
            ax2.legend() #loc='upper right')
            ax2.grid()
            for ax in (ax0, ax1, ax2):
                ax.set_xlim((0.0, system['r_max_u'] + 0.2))
                ax.set_xlabel("r / nm")
                #ax.grid()
                
            g_start = dist_r[np.where(dist_g > 1e-10)[0][0]]
            ax0.set_xlim((0.8*g_start, 1.2*g_start))
            ax1.set_xlim((0.8*g_start, 1.2*g_start))
            ax2.set_xlim((0.8*g_start, 1.2*g_start))
            ax0.set_ylim((0.0, 1.5))
            
        fig.tight_layout()    
        fig.savefig(os.path.join(working_dir_base, "figures", f"core-end_{method.replace('/', '-')}_{system['name'].replace('/', '-')}.png"), dpi=150)
        plt.show()

In [ ]:
for system in systems[1:2]:
    print("system", system['name'])
    working_dir = os.path.join(working_dir_base, system['name'])
    
    with WorkingDir(working_dir):
        dist_r, dist_g, dist_flag = readin_table('ihnc/biinit/A-A.dist.tgt')
        
    fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(5, 2.5))
    ax.plot(dist_r, dist_g, label="g(r)")
    #ax.legend(loc='upper right')
    ax.set_xlim((0.0, system['r_max_u'] + 0.2))
    ax.set_ylim(0.0)
    ax.set_xlabel("r in nm")
    ax.set_ylabel("g(r)")

    fig.tight_layout()    
    fig.savefig("figures/rdf_lj-near-critical.png", dpi=150)
    plt.show()

In [ ]:
for system in systems[1:2]:
    print("system", system['name'])
    working_dir = os.path.join(working_dir_base, system['name'])
    
    fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(5, 2.5))
    
    with WorkingDir(working_dir):
        dist_r, dist_g, dist_flag = readin_table('ihnc/biinit/step_000/A-A.pot.new')
    ax.plot(dist_r, dist_g, label="Low-density approx.", linestyle='--')
    
    with WorkingDir(working_dir):
        dist_r, dist_g, dist_flag = readin_table('ihnc/hncinit/step_000/A-A.pot.new')
    ax.plot(dist_r, dist_g, label="Hypernetted-chain")
    
    ax.legend(loc='upper right')
    ax.set_xlim((0.0, system['r_max_u'] + 0.2))
    ax.set_ylim(-2, 4)
    ax.set_xlabel("r in nm")
    ax.set_ylabel("U(r)")

    fig.tight_layout()    
    fig.savefig("figures/hncinit-biinit_lj-near-critical.png", dpi=150)
    plt.show()

# archive

## inverse settings

In [ ]:
inverse_settings = [
    {'name': 'hncgn-1.5-2-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'gauss-newton',
                'closure': 'hnc',
                'gn-ranges': (1.5, 2.0),  # cut_gn = 1.5 * r_max_u, r_max_g = 2.0 * r_max_u
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': True,
     'iterations-max': 21,
     'system-types': ['spce', 'hexane', 'naphtalene'],
    },
    {'name': 'hncgn-2-2-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'gauss-newton',
                'closure': 'hnc',
                'gn-ranges': (2.0, 2.0),  # cut_gn = 1.5 * r_max_u, r_max_g = 2.0 * r_max_u
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': True,
     'iterations-max': 21,
     'system-types': ['spce', 'hexane', 'naphtalene'],
    },
    {'name': 'hncgn-1.05-2-hncinit-ibiintra',
     'method': {'method': 'iie',
                'algorithm': 'gauss-newton',
                'closure': 'hnc',
                'gn-ranges': (1.05, 2.0),  # cut_gn = 1.5 * r_max_u, r_max_g = 2.0 * r_max_u
                'ignore-intra': False},
     'init': {'method': 'table',
              'table': '.pot.hnc'},
     'intra-treat': 'ibi',
     'extend-g': True,
     'iterations-max': 21,
     'system-types': ['spce', 'hexane', 'naphtalene'],
    },
]

invsets_dict = {invset['name']: invset for invset in inverse_settings}
pd.DataFrame(inverse_settings)